In [144]:
#!/usr/bin/python 
# -*- coding: utf-8 -*-

import torch
import torchvision
from torchvision import transforms, utils
from torch.utils.data import Dataset, DataLoader
import matplotlib.pyplot as plt
import torch.optim as optim
from torch.utils.data import Dataset
import os
from PIL import Image
import matplotlib.pyplot as plt
from torch.optim.lr_scheduler import StepLR
from PIL import Image
import torchxrayvision as xrv
import torch.nn.functional as F
import torch.nn as nn
import numpy as np
from sklearn.metrics import roc_auc_score
import re

torch.cuda.empty_cache()

In [145]:
transform = transforms.Compose([xrv.datasets.XRayCenterCrop(),
                                        xrv.datasets.XRayResizer(224)])

In [146]:
bs = 4

In [147]:
covid19 = xrv.datasets.COVID19_Dataset(
            imgpath='covid_data/images',
            csvpath='covid_data/metadata.csv',
            transform=transform)

# count split sizes
n_train = int(0.8 * len(covid19))
# n_valid_test = len(covid19) - n_train
# n_valid = int(0.5 * n_valid_test)
# n_test = n_valid_test - n_valid
n_test = len(covid19) - n_train

# print(f'Covid Chest x-ray stats dataset stats:\n\n{covid19},\nnumber of training={n_train}, \
# \n number of validing={n_valid} ,\n number of testing={n_test}',flush=True)
print(f'Covid Chest x-ray stats dataset stats:\n\n{covid19},\nnumber of training={n_train}, \
,\n number of testing={n_test}',flush=True)
# split the dataset
# train_set, val_set, test_set = torch.utils.data.random_split(covid19, [n_train, n_valid, n_test])
train_set, test_set = torch.utils.data.random_split(covid19, [n_train, n_test])

{'ARDS': {0.0: 92, 1.0: 4},
 'Bacterial Pneumonia': {0.0: 90, 1.0: 6},
 'COVID-19': {0.0: 23, 1.0: 73},
 'MERS': {0.0: 96},
 'No Finding': {0.0: 95, 1.0: 1},
 'Pneumonia': {0.0: 2, 1.0: 94},
 'SARS': {0.0: 85, 1.0: 11},
 'Streptococcus': {0.0: 90, 1.0: 6},
 'Viral Pneumonia': {0.0: 12, 1.0: 84}}
Covid Chest x-ray stats dataset stats:

COVID19_Dataset num_samples=96,
number of training=76, ,
 number of testing=20


In [148]:
def load_train_data():
    train_loader = torch.utils.data.DataLoader(train_set, batch_size = bs, num_workers = 0, shuffle=True)
    return train_loader

def load_val_data():
    test_loader = torch.utils.data.DataLoader(val_set, batch_size = bs, num_workers = 0, shuffle=False)
    return test_loader

def load_test_data():
    test_loader = torch.utils.data.DataLoader(test_set, batch_size = bs, num_workers = 0, shuffle=False)
    return test_loader

In [149]:

# train_data = xrv.datasets.COVID19_Dataset('covid_data/images', transform=transform)
# # print(train_data[1]["PA"])
# train_loader = torch.utils.data.DataLoader(train_data, batch_size = 64, num_workers = 0, shuffle=True)
# for idx, batch_samples in enumerate(train_loader):
#     print(1)
#     print(idx)
#     text_batchs, text_labels = batch_samples["PA"], batch_samples["lab"]
#     print(text_batchs)
# # dataiter=iter(train_loader)
# # print(dataiter)
# # data=dataiter.next
# # print(data["PA"])

# # images=data
# # print(data)
# # print(type(images),type(labels))
# # print(type(train_loader))

In [150]:
class DenseNetModel(nn.Module):

    def __init__(self):
        """
        Pass in parsed HyperOptArgumentParser to the model
        :param hparams:
        """
        super(DenseNetModel, self).__init__()

        self.dense_net = xrv.models.DenseNet(num_classes=2)
        self.criterion = nn.CrossEntropyLoss()

    def forward(self, x):
        logits = self.dense_net(x)
        return logits
    
model = DenseNetModel().to(device)
print(model)

DenseNetModel(
  (dense_net): DenseNet(
    (features): Sequential(
      (conv0): Conv2d(1, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
      (norm0): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu0): ReLU(inplace=True)
      (pool0): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
      (denseblock1): _DenseBlock(
        (denselayer1): _DenseLayer(
          (norm1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
          (relu1): ReLU(inplace=True)
          (conv1): Conv2d(64, 128, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (norm2): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
          (relu2): ReLU(inplace=True)
          (conv2): Conv2d(128, 32, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        )
        (denselayer2): _DenseLayer(
          (norm1): BatchNorm2d(96, eps=1e-05, mome

In [151]:
# class CNN(nn.Module):
    
#     def __init__(self):
#         super(CNN, self).__init__()           
            
#         self.conv1 = nn.Conv2d(1, 64, kernel_size=11, stride=4, padding=2)
#         self.conv2 = nn.Conv2d(64, 192, kernel_size=5, padding=2)
#         self.conv3 = nn.Conv2d(192, 384, kernel_size=3, padding=1)
#         self.conv4 = nn.Conv2d(384, 256, kernel_size=3, padding=1)
#         self.conv5 = nn.Conv2d(256, 256, kernel_size=3, padding=1)
        
#         self.dropout = nn.Dropout(0.5)        
#         self.activation = nn.RReLU(inplace = True)
        
#         self.pool = nn.AdaptiveAvgPool2d((6,6))
        
#         self.dense1 = nn.Linear(256*6*6, 4096)
#         self.dense2 = nn.Linear(4096, 4096)
#         self.out = nn.Linear(4096, 2)
        
#     def forward(self, x):

#         x = self.conv1(x)
#         x = self.activation(x)
#         x = F.max_pool2d(x, kernel_size=3, stride = 2)
        
#         x = self.conv2(x)
#         x = self.activation(x)
#         x = F.max_pool2d(x, kernel_size=3, stride = 2)
        
#         x = self.conv3(x)
#         x = self.activation(x)
        
#         x = self.conv4(x)
#         x = self.activation(x)
        
#         x = self.conv5(x)
#         x = self.activation(x)
#         x = F.max_pool2d(x, kernel_size=3, stride = 2)
        
#         ########
        
#         x = self.pool(x)
#         x = torch.flatten(x, 1)
        
#         x = self.dropout(x)
#         x = self.dense1(x)
#         x = self.activation(x)
        

#         x = self.dropout(x) 
#         x = self.dense2(x)
#         x = self.activation(x)
#         x = F.log_softmax(x, dim=1)
        
#         return x

In [152]:
def mixup_data(x, y, alpha=1.0, use_cuda=True):
    '''Returns mixed inputs, pairs of targets, and lambda'''
    if alpha > 0:
        lam = np.random.beta(alpha, alpha)
#         print('lam',lam)
    else:
        lam = 1

    batch_size = x.size()[0]
    if use_cuda:
        index = torch.randperm(batch_size).cuda()
    else:
        index = torch.randperm(batch_size)

    mixed_x = lam * x + (1 - lam) * x[index, :]
    y_a, y_b = y, y[index]
    return mixed_x, y_a, y_b, lam

def mixup_criterion(criterion, pred, y_a, y_b, lam):
#     print(pred)
#     print(y_a)
#     print('criterion',criterion(pred, y_a))
    return lam * criterion(pred, y_a) + (1 - lam) * criterion(pred, y_b)

In [166]:
from torch.utils.tensorboard import SummaryWriter
writer = SummaryWriter()

alpha = 1

def train(optimizer, epoch):
    
    model.train()
    train_loader = load_train_data()
    
    train_loss = 0
    train_correct = 0
    
    for batch_index, batch_samples in enumerate(train_loader):
        
        # move data to device
        data, target = batch_samples["PA"].to(device), batch_samples["lab"].to(device)
        data, targets_a, targets_b, lam = mixup_data(data, target.long()[:, 2],
                                                       alpha, use_cuda=True)
        
        
        optimizer.zero_grad()
        output = model(data)
        
#         print(output)
#         print(target.long()[:, 2])
#         loss = nn.functional.nll_loss(output, target.long()[:, 2])
        criteria = nn.CrossEntropyLoss()
#         loss_ = criteria(output, target.long()[:, 2])
        loss = mixup_criterion(criteria, output, targets_a, targets_b, lam)
        train_loss += criteria(output, target.long()[:, 2])
        
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        
        pred = output.argmax(dim=1, keepdim=True)
        train_correct += pred.eq(target.long()[:, 2].view_as(pred)).sum().item()
    
        # Display progress and write to tensorboard
        if batch_index % bs == 0:
            print('Train Epoch: {} [{}/{} ({:.0f}%)]\tTrain Loss: {:.6f}'.format(
                epoch, batch_index, len(train_loader),
                100.0 * batch_index / len(train_loader), loss.item()/ bs))
            f = open('model_result/DenseNet_alpha_{}.txt'.format(alpha), 'a+')
            f.write('Train Epoch: {} [{}/{} ({:.0f}%)]\tTrain Loss: {:.6f}'.format(
                epoch, batch_index, len(train_loader),
                100.0 * batch_index / len(train_loader), loss.item()/ bs))
            f.write('\n')
            f.close()
#             niter = epoch*len(train_loader)+batch_index
#             writer.add_scalar('Train/Loss', loss.data, niter)
    
    print('\nTrain set: Average loss: {:.4f}, Accuracy: {}/{} ({:.0f}%)\n'.format(
        train_loss/len(train_loader.dataset), train_correct, len(train_loader.dataset),
        100.0 * train_correct / len(train_loader.dataset)))
    f = open('model_result/DenseNet_alpha_{}.txt'.format(alpha), 'a+')
    f.write('\nTrain set: Average loss: {:.4f}, Accuracy: {}/{} ({:.0f}%)\n'.format(
        train_loss/len(train_loader.dataset), train_correct, len(train_loader.dataset),
        100.0 * train_correct / len(train_loader.dataset)))
    f.write('\n')
    f.close()

In [163]:
def test(epoch):
    
    model.eval()
    test_loss = 0
    correct = 0
    test_loader = load_test_data()
    results = []
    
    TP = 0
    TN = 0
    FN = 0
    FP = 0
    
    
    criteria = nn.CrossEntropyLoss()
    # Don't update model
    with torch.no_grad():
        tpr_list = []
        fpr_list = []
        
        predlist=[]
        targetlist=[]
        # Predict
        for batch_index, batch_samples in enumerate(test_loader):
            
            data, target = batch_samples["PA"].to(device), batch_samples["lab"].to(device)
            output = model(data)
            
            
            test_loss += criteria(output, target.long()[:, 2])
#             test_loss += F.nll_loss(output, target.long()[:, 2], reduction='sum').item()
            pred = output.argmax(dim=1, keepdim=True)
#             print(pred)
#             print(target.long()[:, 2].view_as(pred))
            correct += pred.eq(target.long()[:, 2].view_as(pred)).sum().item()
#             print(pred.eq(target.long()[:, 2].view_as(pred)))
            TP += ((pred == 1) & (target.long()[:, 2].view_as(pred).data == 1)).cpu().sum()
            TN += ((pred == 0) & (target.long()[:, 2].view_as(pred) == 0)).cpu().sum()
#             # FN    predict 0 label 1
            FN += ((pred == 0) & (target.long()[:, 2].view_as(pred) == 1)).cpu().sum()
#             # FP    predict 1 label 0
            FP += ((pred == 1) & (target.long()[:, 2].view_as(pred) == 0)).cpu().sum()
            print(TP,TN,FN,FP)
            
            
#             print(output[:,1].cpu().numpy())
#             print((output[:,1]+output[:,0]).cpu().numpy())
#             predcpu=(output[:,1].cpu().numpy())/((output[:,1]+output[:,0]).cpu().numpy())
            targetcpu=target.long()[:, 2].cpu().numpy()
            predlist=np.append(predlist, pred.cpu().numpy())
            targetlist=np.append(targetlist,targetcpu)
#             print('pred',predlist)
# #             print('pred2',pred)
#             print('target',targetlist)
            
        print('TP=',TP,'TN=',TN,'FN=',FN,'FP=',FP)
        print('TP+FP',TP+FP)
        p = TP.item() / (TP + FP).item()
        print('precision',p)
        p = TP.item() / (TP + FP).item()
        r = TP.item() / (TP + FN).item()
        print('recall',r)
        F1 = 2 * r * p / (r + p)
        acc = (TP + TN).item() / (TP + TN + FP + FN).item()
        print('F1',F1)
        print('acc',acc)
#         print('pred',predlist)
#         print('target',targetlist)
#         print('pred',predcpu)
#         print('target',targetcpu)
#         print('AUC',roc_auc_score(targetcpu,predcpu))
        AUC = roc_auc_score(targetlist,predlist)
        print('AUC', AUC)
        f = open('model_result/DenseNet_alpha_{}.txt'.format(alpha), 'a+')
        f.write('precision, recall, F1, acc= \n')
        f.writelines(str(p))
        f.writelines('\n')
        f.writelines(str(r))
        f.writelines('\n')
        f.writelines(str(F1))
        f.writelines('\n')
        f.writelines(str(acc))
        f.writelines('\n')
        f.close()
#         try:
#             print('AUC',roc_auc_score(predlist, targetlist))
#         except ValueError:
#             pass
#         tpr = tp/(tp+fn)
#         fpr = fp/(fp+tn)
#         tpr_list.append(tpr)
#         fpr_list.append(fpr)
#         fpr=TP.item() / (FP + TN).item()
#         tpr_list.append(r)
#         fpr_list.append(fpr)
#         print('AUC',np.trapz(tpr_list, fpr_list))
    test_loss /= len(test_loader.dataset)
    

    # Display results
    print('\nTest set: Average loss: {:.4f}, Accuracy: {}/{} ({:.0f}%)\n'.format(
        test_loss, correct, len(test_loader.dataset),
        100.0 * correct / len(test_loader.dataset)))
    
    
    return r, p, acc, AUC
    
    # Write to tensorboard
#     writer.add_scalar('Test Accuracy', 100.0 * correct / len(test_loader.dataset), epoch)

In [155]:
class DenseNet121(nn.Module):
    """Model modified.

    The architecture of our model is the same as standard DenseNet121
    except the classifier layer which has an additional sigmoid function.

    """
    def __init__(self, out_size):
        super(DenseNet121, self).__init__()
        self.densenet121 = torchvision.models.densenet121(pretrained=True)
        num_ftrs = self.densenet121.classifier.in_features
        self.densenet121.classifier = nn.Sequential(
            nn.Linear(num_ftrs, out_size),
            nn.Sigmoid()
        )

    def forward(self, x):
        x = self.densenet121(x)
        return x

In [167]:
#model define

device = 'cuda'

# Tensorboard Writer

CKPT_PATH = 'model.pth.tar'
N_CLASSES = 14

# DenseNet121 = DenseNet121(N_CLASSES).cuda()
# model = CNN().to(device)
model = DenseNetModel().to(device)

In [157]:
CKPT_PATH = './CheXNet/model.pth.tar'

if os.path.isfile(CKPT_PATH):
    print("=> loading checkpoint")
    checkpoint = torch.load(CKPT_PATH)        
    state_dict = checkpoint['state_dict']
    remove_data_parallel = False


    pattern = re.compile(
        r'^(.*denselayer\d+\.(?:norm|relu|conv))\.((?:[12])\.(?:weight|bias|running_mean|running_var))$')
    for key in list(state_dict.keys()):
        match = pattern.match(key)
        new_key = match.group(1) + match.group(2) if match else key
        new_key = new_key[7:] if remove_data_parallel else new_key
        new_key = new_key[7:]
        state_dict[new_key] = state_dict[key]
        del state_dict[key]


    DenseNet121.load_state_dict(checkpoint['state_dict'])
    print("=> loaded checkpoint")
#     print(densenet121)
else:
    print("=> no checkpoint found")
    
DenseNet121.densenet121.classifier._modules['0'] = nn.Linear(in_features=1024, out_features=2, bias=True)
DenseNet121.densenet121.features.conv0 = nn.Conv2d(1, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
print(DenseNet121)
model = DenseNet121.to(device)

=> loading checkpoint
=> loaded checkpoint
DenseNet121(
  (densenet121): DenseNet(
    (features): Sequential(
      (conv0): Conv2d(1, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
      (norm0): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (relu0): ReLU(inplace=True)
      (pool0): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
      (denseblock1): _DenseBlock(
        (denselayer1): _DenseLayer(
          (norm1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
          (relu1): ReLU(inplace=True)
          (conv1): Conv2d(64, 128, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (norm2): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
          (relu2): ReLU(inplace=True)
          (conv2): Conv2d(128, 32, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        )
        (denselayer2): _DenseLayer(
       

In [168]:
# 1dense

r_list = []
p_list = []
acc_list = []
AUC_list = []


#optimizer = optim.SGD(model.parameters(), lr=0.001, momentum = 0.9)
optimizer = optim.Adam(model.parameters(), lr=0.0001)
# scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=10)
scheduler = StepLR(optimizer, step_size=1)

total_epoch = 1000
for epoch in range(1, total_epoch+1):
    train(optimizer, epoch)
    
    r, p, acc, AUC = test(epoch)
    p_list.append(p)
    r_list.append(r)
    acc_list.append(acc)
    AUC_list.append(AUC)

    # Save model
    if epoch == total_epoch:
       torch.save(model.state_dict(), "model_backup/DenseNet_{}.pt".format(epoch))  

    if epoch % 10 == 0:
        r_ave = sum(r_list)/len(r_list)
        p_ave = sum(p_list)/len(p_list)
        acc_ave = sum(acc_list)/len(acc_list)
        AUC_ave = sum(AUC_list)/len(AUC_list)
        F1_ave = 2 * r_ave * p_ave / (r_ave + p_ave)
        r_list = []
        p_list = []
        acc_list = []
        AUC_list = []
        print('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))

        f = open('model_result/DenseNet_alpha_{}.txt'.format(alpha), 'a+')
        f.write('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))
        f.close()
# state = {'epoch': epoch + 1, 'state_dict': model.state_dict(),
#                  'optimizer': optimizer.state_dict(), 'scheduler' : scheduler}
# torch.save(state, "model_backup/AlexNetAdamState")



Train Epoch: 1 [0/19 (0%)]	Train Loss: 0.140894
Train Epoch: 1 [4/19 (21%)]	Train Loss: 0.131018
Train Epoch: 1 [8/19 (42%)]	Train Loss: 0.106658
Train Epoch: 1 [12/19 (63%)]	Train Loss: 0.099173
Train Epoch: 1 [16/19 (84%)]	Train Loss: 0.133357

Train set: Average loss: 0.1295, Accuracy: 57/76 (75%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(0) tensor(0) tensor(1)
tensor(11) tensor(0) tensor(0) tensor(1)
tensor(14) tensor(0) tensor(0) tensor(2)
tensor(16) tensor(0) tensor(0) tensor(4)
TP= tensor(16) TN= tensor(0) FN= tensor(0) FP= tensor(4)
TP+FP tensor(20)
precision 0.8
recall 1.0
F1 0.888888888888889
acc 0.8
AUC 0.5

Test set: Average loss: 0.1009, Accuracy: 16/20 (80%)

Train Epoch: 2 [0/19 (0%)]	Train Loss: 0.081727
Train Epoch: 2 [4/19 (21%)]	Train Loss: 0.224135
Train Epoch: 2 [8/19 (42%)]	Train Loss: 0.208758
Train Epoch: 2 [12/19 (63%)]	Train Loss: 0.187175
Train Epoch: 2 [16/19 (84%)]	Train Loss: 0.063061

Train set: Average loss: 0.1491, Accuracy: 56/76 (74%)


Train Epoch: 12 [16/19 (84%)]	Train Loss: 0.280573

Train set: Average loss: 0.1628, Accuracy: 53/76 (70%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(6) tensor(1) tensor(1) tensor(0)
tensor(10) tensor(1) tensor(1) tensor(0)
tensor(13) tensor(2) tensor(1) tensor(0)
tensor(15) tensor(3) tensor(1) tensor(1)
TP= tensor(15) TN= tensor(3) FN= tensor(1) FP= tensor(1)
TP+FP tensor(16)
precision 0.9375
recall 0.9375
F1 0.9375
acc 0.9
AUC 0.84375

Test set: Average loss: 0.0860, Accuracy: 18/20 (90%)

Train Epoch: 13 [0/19 (0%)]	Train Loss: 0.067046
Train Epoch: 13 [4/19 (21%)]	Train Loss: 0.144882
Train Epoch: 13 [8/19 (42%)]	Train Loss: 0.055856
Train Epoch: 13 [12/19 (63%)]	Train Loss: 0.068199
Train Epoch: 13 [16/19 (84%)]	Train Loss: 0.167054

Train set: Average loss: 0.1252, Accuracy: 59/76 (78%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(6) tensor(1) tensor(1) tensor(0)
tensor(10) tensor(1) tensor(1) tensor(0)
tensor(13) tensor(1) tensor(1) tensor(1)
tensor(14) tensor(1) tensor(

tensor(6) tensor(1) tensor(1) tensor(0)
tensor(10) tensor(1) tensor(1) tensor(0)
tensor(13) tensor(1) tensor(1) tensor(1)
tensor(14) tensor(2) tensor(2) tensor(2)
TP= tensor(14) TN= tensor(2) FN= tensor(2) FP= tensor(2)
TP+FP tensor(16)
precision 0.875
recall 0.875
F1 0.875
acc 0.8
AUC 0.6875

Test set: Average loss: 0.1101, Accuracy: 16/20 (80%)

Train Epoch: 24 [0/19 (0%)]	Train Loss: 0.046032
Train Epoch: 24 [4/19 (21%)]	Train Loss: 0.088743
Train Epoch: 24 [8/19 (42%)]	Train Loss: 0.055605
Train Epoch: 24 [12/19 (63%)]	Train Loss: 0.068156
Train Epoch: 24 [16/19 (84%)]	Train Loss: 0.198506

Train set: Average loss: 0.0831, Accuracy: 68/76 (89%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(6) tensor(1) tensor(1) tensor(0)
tensor(10) tensor(1) tensor(1) tensor(0)
tensor(13) tensor(1) tensor(1) tensor(1)
tensor(15) tensor(2) tensor(1) tensor(2)
TP= tensor(15) TN= tensor(2) FN= tensor(1) FP= tensor(2)
TP+FP tensor(17)
precision 0.8823529411764706
recall 0.9375
F1 0.9090909090909091


Train Epoch: 35 [0/19 (0%)]	Train Loss: 0.099837
Train Epoch: 35 [4/19 (21%)]	Train Loss: 0.066484
Train Epoch: 35 [8/19 (42%)]	Train Loss: 0.103804
Train Epoch: 35 [12/19 (63%)]	Train Loss: 0.135221
Train Epoch: 35 [16/19 (84%)]	Train Loss: 0.144204

Train set: Average loss: 0.1329, Accuracy: 61/76 (80%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(6) tensor(1) tensor(1) tensor(0)
tensor(10) tensor(1) tensor(1) tensor(0)
tensor(13) tensor(1) tensor(1) tensor(1)
tensor(14) tensor(2) tensor(2) tensor(2)
TP= tensor(14) TN= tensor(2) FN= tensor(2) FP= tensor(2)
TP+FP tensor(16)
precision 0.875
recall 0.875
F1 0.875
acc 0.8
AUC 0.6875

Test set: Average loss: 0.0897, Accuracy: 16/20 (80%)

Train Epoch: 36 [0/19 (0%)]	Train Loss: 0.055271
Train Epoch: 36 [4/19 (21%)]	Train Loss: 0.042348
Train Epoch: 36 [8/19 (42%)]	Train Loss: 0.141557
Train Epoch: 36 [12/19 (63%)]	Train Loss: 0.061907
Train Epoch: 36 [16/19 (84%)]	Train Loss: 0.052671

Train set: Average loss: 0.0887, Accuracy: 70/76 (

Train Epoch: 46 [16/19 (84%)]	Train Loss: 0.096673

Train set: Average loss: 0.1382, Accuracy: 61/76 (80%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(1) tensor(0) tensor(0)
tensor(11) tensor(1) tensor(0) tensor(0)
tensor(14) tensor(1) tensor(0) tensor(1)
tensor(16) tensor(2) tensor(0) tensor(2)
TP= tensor(16) TN= tensor(2) FN= tensor(0) FP= tensor(2)
TP+FP tensor(18)
precision 0.8888888888888888
recall 1.0
F1 0.9411764705882353
acc 0.9
AUC 0.75

Test set: Average loss: 0.0949, Accuracy: 18/20 (90%)

Train Epoch: 47 [0/19 (0%)]	Train Loss: 0.037003
Train Epoch: 47 [4/19 (21%)]	Train Loss: 0.037358
Train Epoch: 47 [8/19 (42%)]	Train Loss: 0.049449
Train Epoch: 47 [12/19 (63%)]	Train Loss: 0.150725
Train Epoch: 47 [16/19 (84%)]	Train Loss: 0.042781

Train set: Average loss: 0.0836, Accuracy: 66/76 (87%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(0) tensor(0) tensor(1)
tensor(11) tensor(0) tensor(0) tensor(1)
tensor(14) tensor(0) tensor(0) tensor(2)
tensor(16)

...

Train Epoch: 952 [8/19 (42%)]	Train Loss: 0.007407
Train Epoch: 952 [12/19 (63%)]	Train Loss: 0.072057
Train Epoch: 952 [16/19 (84%)]	Train Loss: 0.000263

Train set: Average loss: 0.1847, Accuracy: 53/76 (70%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(0) tensor(0) tensor(1)
tensor(11) tensor(0) tensor(0) tensor(1)
tensor(14) tensor(1) tensor(0) tensor(1)
tensor(16) tensor(1) tensor(0) tensor(3)
TP= tensor(16) TN= tensor(1) FN= tensor(0) FP= tensor(3)
TP+FP tensor(19)
precision 0.8421052631578947
recall 1.0
F1 0.9142857142857143
acc 0.85
AUC 0.625

Test set: Average loss: 0.0617, Accuracy: 17/20 (85%)

Train Epoch: 953 [0/19 (0%)]	Train Loss: 0.085417
Train Epoch: 953 [4/19 (21%)]	Train Loss: 0.001749
Train Epoch: 953 [8/19 (42%)]	Train Loss: 0.038621
Train Epoch: 953 [12/19 (63%)]	Train Loss: 0.012364
Train Epoch: 953 [16/19 (84%)]	Train Loss: 0.000988

Train set: Average loss: 0.0807, Accuracy: 64/76 (84%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(1) t

Train Epoch: 963 [16/19 (84%)]	Train Loss: 0.003949

Train set: Average loss: 0.1211, Accuracy: 62/76 (82%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(1) tensor(0) tensor(0)
tensor(11) tensor(1) tensor(0) tensor(0)
tensor(14) tensor(2) tensor(0) tensor(0)
tensor(15) tensor(2) tensor(1) tensor(2)
TP= tensor(15) TN= tensor(2) FN= tensor(1) FP= tensor(2)
TP+FP tensor(17)
precision 0.8823529411764706
recall 0.9375
F1 0.9090909090909091
acc 0.85
AUC 0.71875

Test set: Average loss: 0.0679, Accuracy: 17/20 (85%)

Train Epoch: 964 [0/19 (0%)]	Train Loss: 0.057487
Train Epoch: 964 [4/19 (21%)]	Train Loss: 0.001139
Train Epoch: 964 [8/19 (42%)]	Train Loss: 0.020136
Train Epoch: 964 [12/19 (63%)]	Train Loss: 0.083659
Train Epoch: 964 [16/19 (84%)]	Train Loss: 0.086969

Train set: Average loss: 0.0546, Accuracy: 67/76 (88%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(1) tensor(0) tensor(0)
tensor(11) tensor(1) tensor(0) tensor(0)
tensor(14) tensor(2) tensor(0) tensor(

tensor(7) tensor(1) tensor(0) tensor(0)
tensor(11) tensor(1) tensor(0) tensor(0)
tensor(14) tensor(1) tensor(0) tensor(1)
tensor(16) tensor(1) tensor(0) tensor(3)
TP= tensor(16) TN= tensor(1) FN= tensor(0) FP= tensor(3)
TP+FP tensor(19)
precision 0.8421052631578947
recall 1.0
F1 0.9142857142857143
acc 0.85
AUC 0.625

Test set: Average loss: 0.0748, Accuracy: 17/20 (85%)

Train Epoch: 975 [0/19 (0%)]	Train Loss: 0.091958
Train Epoch: 975 [4/19 (21%)]	Train Loss: 0.087734
Train Epoch: 975 [8/19 (42%)]	Train Loss: 0.000986
Train Epoch: 975 [12/19 (63%)]	Train Loss: 0.003387
Train Epoch: 975 [16/19 (84%)]	Train Loss: 0.085167

Train set: Average loss: 0.0860, Accuracy: 64/76 (84%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(1) tensor(0) tensor(0)
tensor(11) tensor(1) tensor(0) tensor(0)
tensor(14) tensor(1) tensor(0) tensor(1)
tensor(16) tensor(2) tensor(0) tensor(2)
TP= tensor(16) TN= tensor(2) FN= tensor(0) FP= tensor(2)
TP+FP tensor(18)
precision 0.8888888888888888
recall 

tensor(14) tensor(1) tensor(0) tensor(1)
tensor(16) tensor(2) tensor(0) tensor(2)
TP= tensor(16) TN= tensor(2) FN= tensor(0) FP= tensor(2)
TP+FP tensor(18)
precision 0.8888888888888888
recall 1.0
F1 0.9411764705882353
acc 0.9
AUC 0.75

Test set: Average loss: 0.0619, Accuracy: 18/20 (90%)

Train Epoch: 986 [0/19 (0%)]	Train Loss: 0.089132
Train Epoch: 986 [4/19 (21%)]	Train Loss: 0.086156
Train Epoch: 986 [8/19 (42%)]	Train Loss: 0.092106
Train Epoch: 986 [12/19 (63%)]	Train Loss: 0.138131
Train Epoch: 986 [16/19 (84%)]	Train Loss: 0.003752

Train set: Average loss: 0.0787, Accuracy: 62/76 (82%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(1) tensor(0) tensor(0)
tensor(11) tensor(1) tensor(0) tensor(0)
tensor(14) tensor(1) tensor(0) tensor(1)
tensor(15) tensor(2) tensor(1) tensor(2)
TP= tensor(15) TN= tensor(2) FN= tensor(1) FP= tensor(2)
TP+FP tensor(17)
precision 0.8823529411764706
recall 0.9375
F1 0.9090909090909091
acc 0.85
AUC 0.71875

Test set: Average loss: 0.0727, 

Train Epoch: 997 [0/19 (0%)]	Train Loss: 0.069110
Train Epoch: 997 [4/19 (21%)]	Train Loss: 0.084371
Train Epoch: 997 [8/19 (42%)]	Train Loss: 0.048889
Train Epoch: 997 [12/19 (63%)]	Train Loss: 0.006886
Train Epoch: 997 [16/19 (84%)]	Train Loss: 0.000301

Train set: Average loss: 0.0620, Accuracy: 68/76 (89%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(1) tensor(0) tensor(0)
tensor(11) tensor(1) tensor(0) tensor(0)
tensor(14) tensor(1) tensor(0) tensor(1)
tensor(16) tensor(1) tensor(0) tensor(3)
TP= tensor(16) TN= tensor(1) FN= tensor(0) FP= tensor(3)
TP+FP tensor(19)
precision 0.8421052631578947
recall 1.0
F1 0.9142857142857143
acc 0.85
AUC 0.625

Test set: Average loss: 0.0761, Accuracy: 17/20 (85%)

Train Epoch: 998 [0/19 (0%)]	Train Loss: 0.056881
Train Epoch: 998 [4/19 (21%)]	Train Loss: 0.003093
Train Epoch: 998 [8/19 (42%)]	Train Loss: 0.003748
Train Epoch: 998 [12/19 (63%)]	Train Loss: 0.003166
Train Epoch: 998 [16/19 (84%)]	Train Loss: 0.108757

Train set: Avera

In [165]:
# 0.6dense

r_list = []
p_list = []
acc_list = []
AUC_list = []


#optimizer = optim.SGD(model.parameters(), lr=0.001, momentum = 0.9)
optimizer = optim.Adam(model.parameters(), lr=0.0001)
# scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=10)
scheduler = StepLR(optimizer, step_size=1)

total_epoch = 1000
for epoch in range(1, total_epoch+1):
    train(optimizer, epoch)
    
    r, p, acc, AUC = test(epoch)
    p_list.append(p)
    r_list.append(r)
    acc_list.append(acc)
    AUC_list.append(AUC)

    # Save model
    if epoch == total_epoch:
       torch.save(model.state_dict(), "model_backup/DenseNet_{}.pt".format(epoch))  

    if epoch % 10 == 0:
        r_ave = sum(r_list)/len(r_list)
        p_ave = sum(p_list)/len(p_list)
        acc_ave = sum(acc_list)/len(acc_list)
        AUC_ave = sum(AUC_list)/len(AUC_list)
        F1_ave = 2 * r_ave * p_ave / (r_ave + p_ave)
        r_list = []
        p_list = []
        acc_list = []
        AUC_list = []
        print('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))

        f = open('model_result/DenseNet_alpha_{}.txt'.format(alpha), 'a+')
        f.write('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))
        f.close()
# state = {'epoch': epoch + 1, 'state_dict': model.state_dict(),
#                  'optimizer': optimizer.state_dict(), 'scheduler' : scheduler}
# torch.save(state, "model_backup/AlexNetAdamState")



Train Epoch: 1 [0/19 (0%)]	Train Loss: 0.131977
Train Epoch: 1 [4/19 (21%)]	Train Loss: 0.142851
Train Epoch: 1 [8/19 (42%)]	Train Loss: 0.140148
Train Epoch: 1 [12/19 (63%)]	Train Loss: 0.229276
Train Epoch: 1 [16/19 (84%)]	Train Loss: 0.161832

Train set: Average loss: 0.1432, Accuracy: 58/76 (76%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(6) tensor(0) tensor(1) tensor(1)
tensor(10) tensor(0) tensor(1) tensor(1)
tensor(13) tensor(0) tensor(1) tensor(2)
tensor(14) tensor(0) tensor(2) tensor(4)
TP= tensor(14) TN= tensor(0) FN= tensor(2) FP= tensor(4)
TP+FP tensor(18)
precision 0.7777777777777778
recall 0.875
F1 0.823529411764706
acc 0.7
AUC 0.4375

Test set: Average loss: 0.1744, Accuracy: 14/20 (70%)

Train Epoch: 2 [0/19 (0%)]	Train Loss: 0.107354
Train Epoch: 2 [4/19 (21%)]	Train Loss: 0.195792
Train Epoch: 2 [8/19 (42%)]	Train Loss: 0.172568
Train Epoch: 2 [12/19 (63%)]	Train Loss: 0.129372
Train Epoch: 2 [16/19 (84%)]	Train Loss: 0.203272

Train set: Average loss: 0.1458, Ac


Train set: Average loss: 0.1383, Accuracy: 59/76 (78%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(6) tensor(0) tensor(1) tensor(1)
tensor(10) tensor(0) tensor(1) tensor(1)
tensor(13) tensor(0) tensor(1) tensor(2)
tensor(15) tensor(1) tensor(1) tensor(3)
TP= tensor(15) TN= tensor(1) FN= tensor(1) FP= tensor(3)
TP+FP tensor(18)
precision 0.8333333333333334
recall 0.9375
F1 0.8823529411764706
acc 0.8
AUC 0.59375

Test set: Average loss: 0.1015, Accuracy: 16/20 (80%)

Train Epoch: 13 [0/19 (0%)]	Train Loss: 0.077551
Train Epoch: 13 [4/19 (21%)]	Train Loss: 0.117587
Train Epoch: 13 [8/19 (42%)]	Train Loss: 0.102017
Train Epoch: 13 [12/19 (63%)]	Train Loss: 0.042597
Train Epoch: 13 [16/19 (84%)]	Train Loss: 0.075465

Train set: Average loss: 0.1490, Accuracy: 56/76 (74%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(6) tensor(1) tensor(1) tensor(0)
tensor(10) tensor(1) tensor(1) tensor(0)
tensor(13) tensor(1) tensor(1) tensor(1)
tensor(15) tensor(2) tensor(1) tensor(2)
TP= tensor(15)

tensor(16) tensor(2) tensor(0) tensor(2)
TP= tensor(16) TN= tensor(2) FN= tensor(0) FP= tensor(2)
TP+FP tensor(18)
precision 0.8888888888888888
recall 1.0
F1 0.9411764705882353
acc 0.9
AUC 0.75

Test set: Average loss: 0.0878, Accuracy: 18/20 (90%)

Train Epoch: 24 [0/19 (0%)]	Train Loss: 0.123320
Train Epoch: 24 [4/19 (21%)]	Train Loss: 0.100210
Train Epoch: 24 [8/19 (42%)]	Train Loss: 0.057877
Train Epoch: 24 [12/19 (63%)]	Train Loss: 0.062546
Train Epoch: 24 [16/19 (84%)]	Train Loss: 0.043951

Train set: Average loss: 0.0933, Accuracy: 68/76 (89%)

tensor(3) tensor(0) tensor(1) tensor(0)
tensor(5) tensor(1) tensor(2) tensor(0)
tensor(9) tensor(1) tensor(2) tensor(0)
tensor(12) tensor(1) tensor(2) tensor(1)
tensor(13) tensor(2) tensor(3) tensor(2)
TP= tensor(13) TN= tensor(2) FN= tensor(3) FP= tensor(2)
TP+FP tensor(15)
precision 0.8666666666666667
recall 0.8125
F1 0.8387096774193549
acc 0.75
AUC 0.65625

Test set: Average loss: 0.1672, Accuracy: 15/20 (75%)

Train Epoch: 25 [0/19 (0

Train Epoch: 35 [0/19 (0%)]	Train Loss: 0.090911
Train Epoch: 35 [4/19 (21%)]	Train Loss: 0.103248
Train Epoch: 35 [8/19 (42%)]	Train Loss: 0.167042
Train Epoch: 35 [12/19 (63%)]	Train Loss: 0.047473
Train Epoch: 35 [16/19 (84%)]	Train Loss: 0.090885

Train set: Average loss: 0.1661, Accuracy: 59/76 (78%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(1) tensor(0) tensor(0)
tensor(11) tensor(1) tensor(0) tensor(0)
tensor(14) tensor(1) tensor(0) tensor(1)
tensor(15) tensor(2) tensor(1) tensor(2)
TP= tensor(15) TN= tensor(2) FN= tensor(1) FP= tensor(2)
TP+FP tensor(17)
precision 0.8823529411764706
recall 0.9375
F1 0.9090909090909091
acc 0.85
AUC 0.71875

Test set: Average loss: 0.0892, Accuracy: 17/20 (85%)

Train Epoch: 36 [0/19 (0%)]	Train Loss: 0.037872
Train Epoch: 36 [4/19 (21%)]	Train Loss: 0.032096
Train Epoch: 36 [8/19 (42%)]	Train Loss: 0.040757
Train Epoch: 36 [12/19 (63%)]	Train Loss: 0.245787
Train Epoch: 36 [16/19 (84%)]	Train Loss: 0.032227

Train set: Average lo


Train set: Average loss: 0.1639, Accuracy: 58/76 (76%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(6) tensor(1) tensor(1) tensor(0)
tensor(10) tensor(1) tensor(1) tensor(0)
tensor(13) tensor(1) tensor(1) tensor(1)
tensor(14) tensor(2) tensor(2) tensor(2)
TP= tensor(14) TN= tensor(2) FN= tensor(2) FP= tensor(2)
TP+FP tensor(16)
precision 0.875
recall 0.875
F1 0.875
acc 0.8
AUC 0.6875

Test set: Average loss: 0.0800, Accuracy: 16/20 (80%)

Train Epoch: 47 [0/19 (0%)]	Train Loss: 0.045256
Train Epoch: 47 [4/19 (21%)]	Train Loss: 0.032896
Train Epoch: 47 [8/19 (42%)]	Train Loss: 0.015693
Train Epoch: 47 [12/19 (63%)]	Train Loss: 0.018466
Train Epoch: 47 [16/19 (84%)]	Train Loss: 0.054811

Train set: Average loss: 0.1374, Accuracy: 64/76 (84%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(0) tensor(0) tensor(1)
tensor(11) tensor(0) tensor(0) tensor(1)
tensor(14) tensor(0) tensor(0) tensor(2)
tensor(16) tensor(1) tensor(0) tensor(3)
TP= tensor(16) TN= tensor(1) FN= tensor(0)

Train Epoch: 58 [0/19 (0%)]	Train Loss: 0.179371
Train Epoch: 58 [4/19 (21%)]	Train Loss: 0.030348
Train Epoch: 58 [8/19 (42%)]	Train Loss: 0.046899
Train Epoch: 58 [12/19 (63%)]	Train Loss: 0.018105
Train Epoch: 58 [16/19 (84%)]	Train Loss: 0.016617

Train set: Average loss: 0.1455, Accuracy: 64/76 (84%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(6) tensor(1) tensor(1) tensor(0)
tensor(10) tensor(1) tensor(1) tensor(0)
tensor(13) tensor(1) tensor(1) tensor(1)
tensor(14) tensor(2) tensor(2) tensor(2)
TP= tensor(14) TN= tensor(2) FN= tensor(2) FP= tensor(2)
TP+FP tensor(16)
precision 0.875
recall 0.875
F1 0.875
acc 0.8
AUC 0.6875

Test set: Average loss: 0.1189, Accuracy: 16/20 (80%)

Train Epoch: 59 [0/19 (0%)]	Train Loss: 0.038008
Train Epoch: 59 [4/19 (21%)]	Train Loss: 0.024545
Train Epoch: 59 [8/19 (42%)]	Train Loss: 0.144583
Train Epoch: 59 [12/19 (63%)]	Train Loss: 0.059956
Train Epoch: 59 [16/19 (84%)]	Train Loss: 0.025628

Train set: Average loss: 0.1415, Accuracy: 64/76 (

KeyboardInterrupt: 

In [158]:
1

r_list = []
p_list = []
acc_list = []
AUC_list = []


#optimizer = optim.SGD(model.parameters(), lr=0.001, momentum = 0.9)
optimizer = optim.Adam(model.parameters(), lr=0.0001)
# scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=10)
scheduler = StepLR(optimizer, step_size=1)

total_epoch = 1000
for epoch in range(1, total_epoch+1):
    train(optimizer, epoch)
    
    r, p, acc, AUC = test(epoch)
    p_list.append(p)
    r_list.append(r)
    acc_list.append(acc)
    AUC_list.append(AUC)

    # Save model
    if epoch == total_epoch:
       torch.save(model.state_dict(), "model_backup/DenseNet_{}.pt".format(epoch))  

    if epoch % 10 == 0:
        r_ave = sum(r_list)/len(r_list)
        p_ave = sum(p_list)/len(p_list)
        acc_ave = sum(acc_list)/len(acc_list)
        AUC_ave = sum(AUC_list)/len(AUC_list)
        F1_ave = 2 * r_ave * p_ave / (r_ave + p_ave)
        r_list = []
        p_list = []
        acc_list = []
        AUC_list = []
        print('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))

        f = open('model_result/DenseNet121_alpha_{}.txt'.format(alpha), 'a+')
        f.write('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))
        f.close()
# state = {'epoch': epoch + 1, 'state_dict': model.state_dict(),
#                  'optimizer': optimizer.state_dict(), 'scheduler' : scheduler}
# torch.save(state, "model_backup/AlexNetAdamState")



Train Epoch: 1 [0/19 (0%)]	Train Loss: 0.169946
Train Epoch: 1 [4/19 (21%)]	Train Loss: 0.166959
Train Epoch: 1 [8/19 (42%)]	Train Loss: 0.184233
Train Epoch: 1 [12/19 (63%)]	Train Loss: 0.151887
Train Epoch: 1 [16/19 (84%)]	Train Loss: 0.148961

Train set: Average loss: 0.1640, Accuracy: 55/76 (72%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(0) tensor(0) tensor(1)
tensor(11) tensor(0) tensor(0) tensor(1)
tensor(14) tensor(0) tensor(0) tensor(2)
tensor(16) tensor(0) tensor(0) tensor(4)
TP= tensor(16) TN= tensor(0) FN= tensor(0) FP= tensor(4)
TP+FP tensor(20)
precision 0.8
recall 1.0
F1 0.888888888888889
acc 0.8
AUC 0.5

Test set: Average loss: 0.1522, Accuracy: 16/20 (80%)

Train Epoch: 2 [0/19 (0%)]	Train Loss: 0.146617
Train Epoch: 2 [4/19 (21%)]	Train Loss: 0.170065
Train Epoch: 2 [8/19 (42%)]	Train Loss: 0.172546
Train Epoch: 2 [12/19 (63%)]	Train Loss: 0.135923
Train Epoch: 2 [16/19 (84%)]	Train Loss: 0.134395

Train set: Average loss: 0.1556, Accuracy: 57/76 (75%)


Train Epoch: 12 [16/19 (84%)]	Train Loss: 0.135813

Train set: Average loss: 0.1215, Accuracy: 65/76 (86%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(5) tensor(1) tensor(2) tensor(0)
tensor(9) tensor(1) tensor(2) tensor(0)
tensor(12) tensor(2) tensor(2) tensor(0)
tensor(13) tensor(3) tensor(3) tensor(1)
TP= tensor(13) TN= tensor(3) FN= tensor(3) FP= tensor(1)
TP+FP tensor(14)
precision 0.9285714285714286
recall 0.8125
F1 0.8666666666666666
acc 0.8
AUC 0.78125

Test set: Average loss: 0.1189, Accuracy: 16/20 (80%)

Train Epoch: 13 [0/19 (0%)]	Train Loss: 0.100456
Train Epoch: 13 [4/19 (21%)]	Train Loss: 0.090627
Train Epoch: 13 [8/19 (42%)]	Train Loss: 0.111396
Train Epoch: 13 [12/19 (63%)]	Train Loss: 0.140677
Train Epoch: 13 [16/19 (84%)]	Train Loss: 0.111105

Train set: Average loss: 0.1167, Accuracy: 68/76 (89%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(1) tensor(0) tensor(0)
tensor(11) tensor(1) tensor(0) tensor(0)
tensor(14) tensor(1) tensor(0) tensor(1)
tenso

tensor(7) tensor(1) tensor(0) tensor(0)
tensor(11) tensor(1) tensor(0) tensor(0)
tensor(14) tensor(1) tensor(0) tensor(1)
tensor(16) tensor(2) tensor(0) tensor(2)
TP= tensor(16) TN= tensor(2) FN= tensor(0) FP= tensor(2)
TP+FP tensor(18)
precision 0.8888888888888888
recall 1.0
F1 0.9411764705882353
acc 0.9
AUC 0.75

Test set: Average loss: 0.1153, Accuracy: 18/20 (90%)

Train Epoch: 24 [0/19 (0%)]	Train Loss: 0.134539
Train Epoch: 24 [4/19 (21%)]	Train Loss: 0.194079
Train Epoch: 24 [8/19 (42%)]	Train Loss: 0.097487
Train Epoch: 24 [12/19 (63%)]	Train Loss: 0.084871
Train Epoch: 24 [16/19 (84%)]	Train Loss: 0.136253

Train set: Average loss: 0.1422, Accuracy: 56/76 (74%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(6) tensor(1) tensor(1) tensor(0)
tensor(10) tensor(1) tensor(1) tensor(0)
tensor(13) tensor(1) tensor(1) tensor(1)
tensor(14) tensor(3) tensor(2) tensor(1)
TP= tensor(14) TN= tensor(3) FN= tensor(2) FP= tensor(1)
TP+FP tensor(15)
precision 0.9333333333333333
recall 0.875
F

Train Epoch: 35 [0/19 (0%)]	Train Loss: 0.079932
Train Epoch: 35 [4/19 (21%)]	Train Loss: 0.104764
Train Epoch: 35 [8/19 (42%)]	Train Loss: 0.091856
Train Epoch: 35 [12/19 (63%)]	Train Loss: 0.086393
Train Epoch: 35 [16/19 (84%)]	Train Loss: 0.083917

Train set: Average loss: 0.1299, Accuracy: 60/76 (79%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(1) tensor(0) tensor(0)
tensor(11) tensor(1) tensor(0) tensor(0)
tensor(14) tensor(1) tensor(0) tensor(1)
tensor(16) tensor(3) tensor(0) tensor(1)
TP= tensor(16) TN= tensor(3) FN= tensor(0) FP= tensor(1)
TP+FP tensor(17)
precision 0.9411764705882353
recall 1.0
F1 0.9696969696969697
acc 0.95
AUC 0.875

Test set: Average loss: 0.0965, Accuracy: 19/20 (95%)

Train Epoch: 36 [0/19 (0%)]	Train Loss: 0.119790
Train Epoch: 36 [4/19 (21%)]	Train Loss: 0.141486
Train Epoch: 36 [8/19 (42%)]	Train Loss: 0.136244
Train Epoch: 36 [12/19 (63%)]	Train Loss: 0.080665
Train Epoch: 36 [16/19 (84%)]	Train Loss: 0.096614

Train set: Average loss: 0

Train Epoch: 46 [12/19 (63%)]	Train Loss: 0.102136
Train Epoch: 46 [16/19 (84%)]	Train Loss: 0.103491

Train set: Average loss: 0.1199, Accuracy: 64/76 (84%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(6) tensor(1) tensor(1) tensor(0)
tensor(10) tensor(1) tensor(1) tensor(0)
tensor(13) tensor(1) tensor(1) tensor(1)
tensor(15) tensor(3) tensor(1) tensor(1)
TP= tensor(15) TN= tensor(3) FN= tensor(1) FP= tensor(1)
TP+FP tensor(16)
precision 0.9375
recall 0.9375
F1 0.9375
acc 0.9
AUC 0.84375

Test set: Average loss: 0.1019, Accuracy: 18/20 (90%)

Train Epoch: 47 [0/19 (0%)]	Train Loss: 0.093049
Train Epoch: 47 [4/19 (21%)]	Train Loss: 0.079351
Train Epoch: 47 [8/19 (42%)]	Train Loss: 0.120215
Train Epoch: 47 [12/19 (63%)]	Train Loss: 0.088257
Train Epoch: 47 [16/19 (84%)]	Train Loss: 0.079692

Train set: Average loss: 0.0989, Accuracy: 71/76 (93%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(6) tensor(1) tensor(1) tensor(0)
tensor(10) tensor(1) tensor(1) tensor(0)
tensor(13) tensor(

...

Train Epoch: 69 [0/19 (0%)]	Train Loss: 0.180531
Train Epoch: 69 [4/19 (21%)]	Train Loss: 0.127293
Train Epoch: 69 [8/19 (42%)]	Train Loss: 0.080448
Train Epoch: 69 [12/19 (63%)]	Train Loss: 0.078719
Train Epoch: 69 [16/19 (84%)]	Train Loss: 0.094424

Train set: Average loss: 0.1127, Accuracy: 66/76 (87%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(1) tensor(0) tensor(0)
tensor(11) tensor(1) tensor(0) tensor(0)
tensor(14) tensor(1) tensor(0) tensor(1)
tensor(15) tensor(2) tensor(1) tensor(2)
TP= tensor(15) TN= tensor(2) FN= tensor(1) FP= tensor(2)
TP+FP tensor(17)
precision 0.8823529411764706
recall 0.9375
F1 0.9090909090909091
acc 0.85
AUC 0.71875

Test set: Average loss: 0.1064, Accuracy: 17/20 (85%)

Train Epoch: 70 [0/19 (0%)]	Train Loss: 0.119388
Train Epoch: 70 [4/19 (21%)]	Train Loss: 0.078755
Train Epoch: 70 [8/19 (42%)]	Train Loss: 0.132915
Train Epoch: 70 [12/19 (63%)]	Train Loss: 0.127490
Train Epoch: 70 [16/19 (84%)]	Train Loss: 0.080392

Train set: Average lo

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(0) tensor(0) tensor(1)
tensor(11) tensor(0) tensor(0) tensor(1)
tensor(14) tensor(0) tensor(0) tensor(2)
tensor(16) tensor(1) tensor(0) tensor(3)
TP= tensor(16) TN= tensor(1) FN= tensor(0) FP= tensor(3)
TP+FP tensor(19)
precision 0.8421052631578947
recall 1.0
F1 0.9142857142857143
acc 0.85
AUC 0.625

Test set: Average loss: 0.1122, Accuracy: 17/20 (85%)


 The epoch is 80, average recall: 0.9688, average precision: 0.9783,average F1: 0.9735, average accuracy: 0.9550, average AUC: 0.9344
Train Epoch: 81 [0/19 (0%)]	Train Loss: 0.126643
Train Epoch: 81 [4/19 (21%)]	Train Loss: 0.081698
Train Epoch: 81 [8/19 (42%)]	Train Loss: 0.079354
Train Epoch: 81 [12/19 (63%)]	Train Loss: 0.103299
Train Epoch: 81 [16/19 (84%)]	Train Loss: 0.079916

Train set: Average loss: 0.1207, Accuracy: 62/76 (82%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(1) tensor(0) tensor(0)
tensor(11) tensor(1) tensor(0) tensor(0)
tensor(14) tensor(1) t

tensor(5) tensor(1) tensor(2) tensor(0)
tensor(9) tensor(1) tensor(2) tensor(0)
tensor(12) tensor(2) tensor(2) tensor(0)
tensor(13) tensor(4) tensor(3) tensor(0)
TP= tensor(13) TN= tensor(4) FN= tensor(3) FP= tensor(0)
TP+FP tensor(13)
precision 1.0
recall 0.8125
F1 0.896551724137931
acc 0.85
AUC 0.90625

Test set: Average loss: 0.1176, Accuracy: 17/20 (85%)

Train Epoch: 92 [0/19 (0%)]	Train Loss: 0.140834
Train Epoch: 92 [4/19 (21%)]	Train Loss: 0.115421
Train Epoch: 92 [8/19 (42%)]	Train Loss: 0.127745
Train Epoch: 92 [12/19 (63%)]	Train Loss: 0.080351
Train Epoch: 92 [16/19 (84%)]	Train Loss: 0.078943

Train set: Average loss: 0.1161, Accuracy: 64/76 (84%)

tensor(3) tensor(0) tensor(1) tensor(0)
tensor(5) tensor(1) tensor(2) tensor(0)
tensor(9) tensor(1) tensor(2) tensor(0)
tensor(12) tensor(1) tensor(2) tensor(1)
tensor(13) tensor(3) tensor(3) tensor(1)
TP= tensor(13) TN= tensor(3) FN= tensor(3) FP= tensor(1)
TP+FP tensor(14)
precision 0.9285714285714286
recall 0.8125
F1 0.866666

Train Epoch: 103 [0/19 (0%)]	Train Loss: 0.079129
Train Epoch: 103 [4/19 (21%)]	Train Loss: 0.126157
Train Epoch: 103 [8/19 (42%)]	Train Loss: 0.126740
Train Epoch: 103 [12/19 (63%)]	Train Loss: 0.103788
Train Epoch: 103 [16/19 (84%)]	Train Loss: 0.079119

Train set: Average loss: 0.1053, Accuracy: 68/76 (89%)

tensor(4) tensor(0) tensor(0) tensor(0)
tensor(7) tensor(1) tensor(0) tensor(0)
tensor(11) tensor(1) tensor(0) tensor(0)
tensor(14) tensor(1) tensor(0) tensor(1)
tensor(16) tensor(2) tensor(0) tensor(2)
TP= tensor(16) TN= tensor(2) FN= tensor(0) FP= tensor(2)
TP+FP tensor(18)
precision 0.8888888888888888
recall 1.0
F1 0.9411764705882353
acc 0.9
AUC 0.75

Test set: Average loss: 0.1073, Accuracy: 18/20 (90%)

Train Epoch: 104 [0/19 (0%)]	Train Loss: 0.079030
Train Epoch: 104 [4/19 (21%)]	Train Loss: 0.125782
Train Epoch: 104 [8/19 (42%)]	Train Loss: 0.079440
Train Epoch: 104 [12/19 (63%)]	Train Loss: 0.078920
Train Epoch: 104 [16/19 (84%)]	Train Loss: 0.119551

Train set: Average

KeyboardInterrupt: 

In [ ]:
0.4

r_list = []
p_list = []
acc_list = []
AUC_list = []


#optimizer = optim.SGD(model.parameters(), lr=0.001, momentum = 0.9)
optimizer = optim.Adam(model.parameters(), lr=0.0001)
# scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=10)
scheduler = StepLR(optimizer, step_size=1)

total_epoch = 1000
for epoch in range(1, total_epoch+1):
    train(optimizer, epoch)
    
    r, p, acc, AUC = test(epoch)
    p_list.append(p)
    r_list.append(r)
    acc_list.append(acc)
    AUC_list.append(AUC)

    # Save model
    if epoch == total_epoch:
       torch.save(model.state_dict(), "model_backup/DenseNet_{}.pt".format(epoch))  

    if epoch % 10 == 0:
        r_ave = sum(r_list)/len(r_list)
        p_ave = sum(p_list)/len(p_list)
        acc_ave = sum(acc_list)/len(acc_list)
        AUC_ave = sum(AUC_list)/len(AUC_list)
        F1_ave = 2 * r_ave * p_ave / (r_ave + p_ave)
        r_list = []
        p_list = []
        acc_list = []
        AUC_list = []
        print('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))

        f = open('model_result/DenseNet121_alpha_{}.txt'.format(alpha), 'a+')
        f.write('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))
        f.close()
# state = {'epoch': epoch + 1, 'state_dict': model.state_dict(),
#                  'optimizer': optimizer.state_dict(), 'scheduler' : scheduler}
# torch.save(state, "model_backup/AlexNetAdamState")



Train Epoch: 1 [0/19 (0%)]	Train Loss: 0.080429
Train Epoch: 1 [4/19 (21%)]	Train Loss: 0.078555
Train Epoch: 1 [8/19 (42%)]	Train Loss: 0.079035
Train Epoch: 1 [12/19 (63%)]	Train Loss: 0.078538
Train Epoch: 1 [16/19 (84%)]	Train Loss: 0.102301

Train set: Average loss: 0.1057, Accuracy: 68/76 (89%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(2) tensor(0) tensor(1)
tensor(11) tensor(2) tensor(2) tensor(1)
tensor(15) tensor(2) tensor(2) tensor(1)
TP= tensor(15) TN= tensor(2) FN= tensor(2) FP= tensor(1)
TP+FP tensor(16)
precision 0.9375
recall 0.8823529411764706
F1 0.9090909090909091
acc 0.85
AUC 0.7745098039215688

Test set: Average loss: 0.1105, Accuracy: 17/20 (85%)

Train Epoch: 2 [0/19 (0%)]	Train Loss: 0.078734
Train Epoch: 2 [4/19 (21%)]	Train Loss: 0.085690
Train Epoch: 2 [8/19 (42%)]	Train Loss: 0.078381
Train Epoch: 2 [12/19 (63%)]	Train Loss: 0.100365
Train Epoch: 2 [16/19 (84%)]	Train Loss: 0.096678

Train set: Average lo

Train Epoch: 12 [0/19 (0%)]	Train Loss: 0.083120
Train Epoch: 12 [4/19 (21%)]	Train Loss: 0.080187
Train Epoch: 12 [8/19 (42%)]	Train Loss: 0.143036
Train Epoch: 12 [12/19 (63%)]	Train Loss: 0.078724
Train Epoch: 12 [16/19 (84%)]	Train Loss: 0.078848

Train set: Average loss: 0.1166, Accuracy: 64/76 (84%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(2) tensor(0) tensor(1)
tensor(11) tensor(2) tensor(2) tensor(1)
tensor(15) tensor(2) tensor(2) tensor(1)
TP= tensor(15) TN= tensor(2) FN= tensor(2) FP= tensor(1)
TP+FP tensor(16)
precision 0.9375
recall 0.8823529411764706
F1 0.9090909090909091
acc 0.85
AUC 0.7745098039215688

Test set: Average loss: 0.1180, Accuracy: 17/20 (85%)

Train Epoch: 13 [0/19 (0%)]	Train Loss: 0.080702
Train Epoch: 13 [4/19 (21%)]	Train Loss: 0.079855
Train Epoch: 13 [8/19 (42%)]	Train Loss: 0.131900
Train Epoch: 13 [12/19 (63%)]	Train Loss: 0.100535
Train Epoch: 13 [16/19 (84%)]	Train Loss: 0.082057

Train set: 

Train Epoch: 23 [0/19 (0%)]	Train Loss: 0.078484
Train Epoch: 23 [4/19 (21%)]	Train Loss: 0.078674
Train Epoch: 23 [8/19 (42%)]	Train Loss: 0.109502
Train Epoch: 23 [12/19 (63%)]	Train Loss: 0.089017
Train Epoch: 23 [16/19 (84%)]	Train Loss: 0.093629

Train set: Average loss: 0.1208, Accuracy: 63/76 (83%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(2) tensor(0) tensor(1)
tensor(12) tensor(2) tensor(1) tensor(1)
tensor(16) tensor(2) tensor(1) tensor(1)
TP= tensor(16) TN= tensor(2) FN= tensor(1) FP= tensor(1)
TP+FP tensor(17)
precision 0.9411764705882353
recall 0.9411764705882353
F1 0.9411764705882353
acc 0.9
AUC 0.803921568627451

Test set: Average loss: 0.1019, Accuracy: 18/20 (90%)

Train Epoch: 24 [0/19 (0%)]	Train Loss: 0.124281
Train Epoch: 24 [4/19 (21%)]	Train Loss: 0.078382
Train Epoch: 24 [8/19 (42%)]	Train Loss: 0.078518
Train Epoch: 24 [12/19 (63%)]	Train Loss: 0.103171
Train Epoch: 24 [16/19 (84%)]	Train Loss: 0.078768

T

Train Epoch: 34 [0/19 (0%)]	Train Loss: 0.078420
Train Epoch: 34 [4/19 (21%)]	Train Loss: 0.094120
Train Epoch: 34 [8/19 (42%)]	Train Loss: 0.129365
Train Epoch: 34 [12/19 (63%)]	Train Loss: 0.078496
Train Epoch: 34 [16/19 (84%)]	Train Loss: 0.087173

Train set: Average loss: 0.0987, Accuracy: 70/76 (92%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(3) tensor(0) tensor(0)
tensor(11) tensor(3) tensor(2) tensor(0)
tensor(15) tensor(3) tensor(2) tensor(0)
TP= tensor(15) TN= tensor(3) FN= tensor(2) FP= tensor(0)
TP+FP tensor(15)
precision 1.0
recall 0.8823529411764706
F1 0.9375
acc 0.9
AUC 0.9411764705882353

Test set: Average loss: 0.1015, Accuracy: 18/20 (90%)

Train Epoch: 35 [0/19 (0%)]	Train Loss: 0.093093
Train Epoch: 35 [4/19 (21%)]	Train Loss: 0.083582
Train Epoch: 35 [8/19 (42%)]	Train Loss: 0.097294
Train Epoch: 35 [12/19 (63%)]	Train Loss: 0.087298
Train Epoch: 35 [16/19 (84%)]	Train Loss: 0.080103

Train set: Average loss: 0.

Train Epoch: 45 [8/19 (42%)]	Train Loss: 0.097594
Train Epoch: 45 [12/19 (63%)]	Train Loss: 0.092133
Train Epoch: 45 [16/19 (84%)]	Train Loss: 0.087290

Train set: Average loss: 0.1007, Accuracy: 69/76 (91%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(3) tensor(0) tensor(0)
tensor(11) tensor(3) tensor(2) tensor(0)
tensor(15) tensor(3) tensor(2) tensor(0)
TP= tensor(15) TN= tensor(3) FN= tensor(2) FP= tensor(0)
TP+FP tensor(15)
precision 1.0
recall 0.8823529411764706
F1 0.9375
acc 0.9
AUC 0.9411764705882353

Test set: Average loss: 0.1039, Accuracy: 18/20 (90%)

Train Epoch: 46 [0/19 (0%)]	Train Loss: 0.078469
Train Epoch: 46 [4/19 (21%)]	Train Loss: 0.106006
Train Epoch: 46 [8/19 (42%)]	Train Loss: 0.078448
Train Epoch: 46 [12/19 (63%)]	Train Loss: 0.096456
Train Epoch: 46 [16/19 (84%)]	Train Loss: 0.078370

Train set: Average loss: 0.1110, Accuracy: 66/76 (87%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) 

...

Train Epoch: 287 [0/19 (0%)]	Train Loss: 0.094147
Train Epoch: 287 [4/19 (21%)]	Train Loss: 0.115721
Train Epoch: 287 [8/19 (42%)]	Train Loss: 0.104028
Train Epoch: 287 [12/19 (63%)]	Train Loss: 0.078336
Train Epoch: 287 [16/19 (84%)]	Train Loss: 0.078408

Train set: Average loss: 0.1046, Accuracy: 68/76 (89%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(3) tensor(0) tensor(0)
tensor(11) tensor(3) tensor(2) tensor(0)
tensor(14) tensor(3) tensor(3) tensor(0)
TP= tensor(14) TN= tensor(3) FN= tensor(3) FP= tensor(0)
TP+FP tensor(14)
precision 1.0
recall 0.8235294117647058
F1 0.9032258064516129
acc 0.85
AUC 0.9117647058823529

Test set: Average loss: 0.1143, Accuracy: 17/20 (85%)

Train Epoch: 288 [0/19 (0%)]	Train Loss: 0.078853
Train Epoch: 288 [4/19 (21%)]	Train Loss: 0.087312
Train Epoch: 288 [8/19 (42%)]	Train Loss: 0.078369
Train Epoch: 288 [12/19 (63%)]	Train Loss: 0.165042
Train Epoch: 288 [16/19 (84%)]	Train Loss: 0.087114

Trai

Train Epoch: 298 [0/19 (0%)]	Train Loss: 0.078345
Train Epoch: 298 [4/19 (21%)]	Train Loss: 0.078336
Train Epoch: 298 [8/19 (42%)]	Train Loss: 0.086948
Train Epoch: 298 [12/19 (63%)]	Train Loss: 0.079286
Train Epoch: 298 [16/19 (84%)]	Train Loss: 0.108935

Train set: Average loss: 0.1054, Accuracy: 68/76 (89%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(2) tensor(0) tensor(1)
tensor(11) tensor(2) tensor(2) tensor(1)
tensor(15) tensor(2) tensor(2) tensor(1)
TP= tensor(15) TN= tensor(2) FN= tensor(2) FP= tensor(1)
TP+FP tensor(16)
precision 0.9375
recall 0.8823529411764706
F1 0.9090909090909091
acc 0.85
AUC 0.7745098039215688

Test set: Average loss: 0.1162, Accuracy: 17/20 (85%)

Train Epoch: 299 [0/19 (0%)]	Train Loss: 0.120793
Train Epoch: 299 [4/19 (21%)]	Train Loss: 0.078718
Train Epoch: 299 [8/19 (42%)]	Train Loss: 0.079035
Train Epoch: 299 [12/19 (63%)]	Train Loss: 0.125665
Train Epoch: 299 [16/19 (84%)]	Train Loss: 0.078332

T

Train Epoch: 309 [0/19 (0%)]	Train Loss: 0.202519
Train Epoch: 309 [4/19 (21%)]	Train Loss: 0.090210
Train Epoch: 309 [8/19 (42%)]	Train Loss: 0.128063
Train Epoch: 309 [12/19 (63%)]	Train Loss: 0.102132
Train Epoch: 309 [16/19 (84%)]	Train Loss: 0.078389

Train set: Average loss: 0.1119, Accuracy: 66/76 (87%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(2) tensor(0) tensor(1)
tensor(11) tensor(2) tensor(2) tensor(1)
tensor(15) tensor(2) tensor(2) tensor(1)
TP= tensor(15) TN= tensor(2) FN= tensor(2) FP= tensor(1)
TP+FP tensor(16)
precision 0.9375
recall 0.8823529411764706
F1 0.9090909090909091
acc 0.85
AUC 0.7745098039215688

Test set: Average loss: 0.1188, Accuracy: 17/20 (85%)

Train Epoch: 310 [0/19 (0%)]	Train Loss: 0.088524
Train Epoch: 310 [4/19 (21%)]	Train Loss: 0.078793
Train Epoch: 310 [8/19 (42%)]	Train Loss: 0.086521
Train Epoch: 310 [12/19 (63%)]	Train Loss: 0.160870
Train Epoch: 310 [16/19 (84%)]	Train Loss: 0.078668

T

Train Epoch: 320 [4/19 (21%)]	Train Loss: 0.078523
Train Epoch: 320 [8/19 (42%)]	Train Loss: 0.078490
Train Epoch: 320 [12/19 (63%)]	Train Loss: 0.078317
Train Epoch: 320 [16/19 (84%)]	Train Loss: 0.079013

Train set: Average loss: 0.1273, Accuracy: 61/76 (80%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(3) tensor(0) tensor(0)
tensor(13) tensor(3) tensor(0) tensor(0)
tensor(17) tensor(3) tensor(0) tensor(0)
TP= tensor(17) TN= tensor(3) FN= tensor(0) FP= tensor(0)
TP+FP tensor(17)
precision 1.0
recall 1.0
F1 1.0
acc 1.0
AUC 1.0

Test set: Average loss: 0.0850, Accuracy: 20/20 (100%)


 The epoch is 320, average recall: 0.9059, average precision: 0.9826,average F1: 0.9427, average accuracy: 0.9050, average AUC: 0.9029
Train Epoch: 321 [0/19 (0%)]	Train Loss: 0.078329
Train Epoch: 321 [4/19 (21%)]	Train Loss: 0.079098
Train Epoch: 321 [8/19 (42%)]	Train Loss: 0.078992
Train Epoch: 321 [12/19 (63%)]	Train Loss: 0.078470
Train Epoch: 321

Train Epoch: 331 [8/19 (42%)]	Train Loss: 0.078409
Train Epoch: 331 [12/19 (63%)]	Train Loss: 0.078560
Train Epoch: 331 [16/19 (84%)]	Train Loss: 0.095006

Train set: Average loss: 0.0915, Accuracy: 72/76 (95%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(3) tensor(0) tensor(0)
tensor(10) tensor(3) tensor(3) tensor(0)
tensor(14) tensor(3) tensor(3) tensor(0)
TP= tensor(14) TN= tensor(3) FN= tensor(3) FP= tensor(0)
TP+FP tensor(14)
precision 1.0
recall 0.8235294117647058
F1 0.9032258064516129
acc 0.85
AUC 0.9117647058823529

Test set: Average loss: 0.1155, Accuracy: 17/20 (85%)

Train Epoch: 332 [0/19 (0%)]	Train Loss: 0.120486
Train Epoch: 332 [4/19 (21%)]	Train Loss: 0.199391
Train Epoch: 332 [8/19 (42%)]	Train Loss: 0.078539
Train Epoch: 332 [12/19 (63%)]	Train Loss: 0.080635
Train Epoch: 332 [16/19 (84%)]	Train Loss: 0.101167

Train set: Average loss: 0.1249, Accuracy: 62/76 (82%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6)

In [141]:
32

r_list = []
p_list = []
acc_list = []
AUC_list = []


#optimizer = optim.SGD(model.parameters(), lr=0.001, momentum = 0.9)
optimizer = optim.Adam(model.parameters(), lr=0.0001)
# scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=10)
scheduler = StepLR(optimizer, step_size=1)

total_epoch = 1000
for epoch in range(1, total_epoch+1):
    train(optimizer, epoch)
    
    r, p, acc, AUC = test(epoch)
    p_list.append(p)
    r_list.append(r)
    acc_list.append(acc)
    AUC_list.append(AUC)

    # Save model
    if epoch == total_epoch:
       torch.save(model.state_dict(), "model_backup/DenseNet_{}.pt".format(epoch))  

    if epoch % 10 == 0:
        r_ave = sum(r_list)/len(r_list)
        p_ave = sum(p_list)/len(p_list)
        acc_ave = sum(acc_list)/len(acc_list)
        AUC_ave = sum(AUC_list)/len(AUC_list)
        F1_ave = 2 * r_ave * p_ave / (r_ave + p_ave)
        r_list = []
        p_list = []
        acc_list = []
        AUC_list = []
        print('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))

        f = open('model_result/DenseNet121_alpha_{}.txt'.format(alpha), 'a+')
        f.write('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))
        f.close()
# state = {'epoch': epoch + 1, 'state_dict': model.state_dict(),
#                  'optimizer': optimizer.state_dict(), 'scheduler' : scheduler}
# torch.save(state, "model_backup/AlexNetAdamState")



Train Epoch: 1 [0/19 (0%)]	Train Loss: 0.078401
Train Epoch: 1 [4/19 (21%)]	Train Loss: 0.078468
Train Epoch: 1 [8/19 (42%)]	Train Loss: 0.141549
Train Epoch: 1 [12/19 (63%)]	Train Loss: 0.128844
Train Epoch: 1 [16/19 (84%)]	Train Loss: 0.137625

Train set: Average loss: 0.1004, Accuracy: 68/76 (89%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(2) tensor(0) tensor(1)
tensor(12) tensor(2) tensor(1) tensor(1)
tensor(14) tensor(2) tensor(3) tensor(1)
TP= tensor(14) TN= tensor(2) FN= tensor(3) FP= tensor(1)
TP+FP tensor(15)
precision 0.9333333333333333
recall 0.8235294117647058
F1 0.8749999999999999
acc 0.8
AUC 0.7450980392156863

Test set: Average loss: 0.1121, Accuracy: 16/20 (80%)

Train Epoch: 2 [0/19 (0%)]	Train Loss: 0.079552
Train Epoch: 2 [4/19 (21%)]	Train Loss: 0.078568
Train Epoch: 2 [8/19 (42%)]	Train Loss: 0.078746
Train Epoch: 2 [12/19 (63%)]	Train Loss: 0.129144
Train Epoch: 2 [16/19 (84%)]	Train Loss: 0.128518

Train set:

Train Epoch: 12 [0/19 (0%)]	Train Loss: 0.078414
Train Epoch: 12 [4/19 (21%)]	Train Loss: 0.131470
Train Epoch: 12 [8/19 (42%)]	Train Loss: 0.078458
Train Epoch: 12 [12/19 (63%)]	Train Loss: 0.082161
Train Epoch: 12 [16/19 (84%)]	Train Loss: 0.131413

Train set: Average loss: 0.1107, Accuracy: 66/76 (87%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(1) tensor(0) tensor(1)
tensor(9) tensor(1) tensor(0) tensor(2)
tensor(13) tensor(1) tensor(0) tensor(2)
tensor(17) tensor(1) tensor(0) tensor(2)
TP= tensor(17) TN= tensor(1) FN= tensor(0) FP= tensor(2)
TP+FP tensor(19)
precision 0.8947368421052632
recall 1.0
F1 0.9444444444444444
acc 0.9
AUC 0.6666666666666667

Test set: Average loss: 0.1077, Accuracy: 18/20 (90%)

Train Epoch: 13 [0/19 (0%)]	Train Loss: 0.078680
Train Epoch: 13 [4/19 (21%)]	Train Loss: 0.126920
Train Epoch: 13 [8/19 (42%)]	Train Loss: 0.133210
Train Epoch: 13 [12/19 (63%)]	Train Loss: 0.079052
Train Epoch: 13 [16/19 (84%)]	Train Loss: 0.078417

Train set: Aver

Train Epoch: 23 [0/19 (0%)]	Train Loss: 0.081708
Train Epoch: 23 [4/19 (21%)]	Train Loss: 0.078487
Train Epoch: 23 [8/19 (42%)]	Train Loss: 0.078614
Train Epoch: 23 [12/19 (63%)]	Train Loss: 0.127345
Train Epoch: 23 [16/19 (84%)]	Train Loss: 0.190691

Train set: Average loss: 0.1229, Accuracy: 61/76 (80%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(1) tensor(0) tensor(1)
tensor(9) tensor(1) tensor(0) tensor(2)
tensor(12) tensor(1) tensor(1) tensor(2)
tensor(16) tensor(1) tensor(1) tensor(2)
TP= tensor(16) TN= tensor(1) FN= tensor(1) FP= tensor(2)
TP+FP tensor(18)
precision 0.8888888888888888
recall 0.9411764705882353
F1 0.9142857142857143
acc 0.85
AUC 0.6372549019607843

Test set: Average loss: 0.1112, Accuracy: 17/20 (85%)

Train Epoch: 24 [0/19 (0%)]	Train Loss: 0.128101
Train Epoch: 24 [4/19 (21%)]	Train Loss: 0.134991
Train Epoch: 24 [8/19 (42%)]	Train Loss: 0.078606
Train Epoch: 24 [12/19 (63%)]	Train Loss: 0.124521
Train Epoch: 24 [16/19 (84%)]	Train Loss: 0.138090


Train Epoch: 34 [0/19 (0%)]	Train Loss: 0.137497
Train Epoch: 34 [4/19 (21%)]	Train Loss: 0.137878
Train Epoch: 34 [8/19 (42%)]	Train Loss: 0.078595
Train Epoch: 34 [12/19 (63%)]	Train Loss: 0.078898
Train Epoch: 34 [16/19 (84%)]	Train Loss: 0.078482

Train set: Average loss: 0.1169, Accuracy: 64/76 (84%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(3) tensor(0) tensor(0)
tensor(11) tensor(3) tensor(2) tensor(0)
tensor(14) tensor(3) tensor(3) tensor(0)
TP= tensor(14) TN= tensor(3) FN= tensor(3) FP= tensor(0)
TP+FP tensor(14)
precision 1.0
recall 0.8235294117647058
F1 0.9032258064516129
acc 0.85
AUC 0.9117647058823529

Test set: Average loss: 0.1124, Accuracy: 17/20 (85%)

Train Epoch: 35 [0/19 (0%)]	Train Loss: 0.132848
Train Epoch: 35 [4/19 (21%)]	Train Loss: 0.078674
Train Epoch: 35 [8/19 (42%)]	Train Loss: 0.134045
Train Epoch: 35 [12/19 (63%)]	Train Loss: 0.118128
Train Epoch: 35 [16/19 (84%)]	Train Loss: 0.141149

Train set: Ave

KeyboardInterrupt: 

In [139]:
0.2

r_list = []
p_list = []
acc_list = []
AUC_list = []


#optimizer = optim.SGD(model.parameters(), lr=0.001, momentum = 0.9)
optimizer = optim.Adam(model.parameters(), lr=0.0001)
# scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=10)
scheduler = StepLR(optimizer, step_size=1)

total_epoch = 1000
for epoch in range(1, total_epoch+1):
    train(optimizer, epoch)
    
    r, p, acc, AUC = test(epoch)
    p_list.append(p)
    r_list.append(r)
    acc_list.append(acc)
    AUC_list.append(AUC)

    # Save model
    if epoch == total_epoch:
       torch.save(model.state_dict(), "model_backup/DenseNet_{}.pt".format(epoch))  

    if epoch % 10 == 0:
        r_ave = sum(r_list)/len(r_list)
        p_ave = sum(p_list)/len(p_list)
        acc_ave = sum(acc_list)/len(acc_list)
        AUC_ave = sum(AUC_list)/len(AUC_list)
        F1_ave = 2 * r_ave * p_ave / (r_ave + p_ave)
        r_list = []
        p_list = []
        acc_list = []
        AUC_list = []
        print('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))

        f = open('model_result/DenseNet121_alpha_{}.txt'.format(alpha), 'a+')
        f.write('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))
        f.close()
# state = {'epoch': epoch + 1, 'state_dict': model.state_dict(),
#                  'optimizer': optimizer.state_dict(), 'scheduler' : scheduler}
# torch.save(state, "model_backup/AlexNetAdamState")



Train Epoch: 1 [0/19 (0%)]	Train Loss: 0.108608
Train Epoch: 1 [4/19 (21%)]	Train Loss: 0.093567
Train Epoch: 1 [8/19 (42%)]	Train Loss: 0.078540
Train Epoch: 1 [12/19 (63%)]	Train Loss: 0.078555
Train Epoch: 1 [16/19 (84%)]	Train Loss: 0.082969

Train set: Average loss: 0.1365, Accuracy: 59/76 (78%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(3) tensor(0) tensor(0)
tensor(12) tensor(3) tensor(1) tensor(0)
tensor(16) tensor(3) tensor(1) tensor(0)
TP= tensor(16) TN= tensor(3) FN= tensor(1) FP= tensor(0)
TP+FP tensor(16)
precision 1.0
recall 0.9411764705882353
F1 0.9696969696969697
acc 0.95
AUC 0.9705882352941176

Test set: Average loss: 0.1019, Accuracy: 19/20 (95%)

Train Epoch: 2 [0/19 (0%)]	Train Loss: 0.080804
Train Epoch: 2 [4/19 (21%)]	Train Loss: 0.090636
Train Epoch: 2 [8/19 (42%)]	Train Loss: 0.079319
Train Epoch: 2 [12/19 (63%)]	Train Loss: 0.080934
Train Epoch: 2 [16/19 (84%)]	Train Loss: 0.078641

Train set: Average loss:

Train Epoch: 12 [0/19 (0%)]	Train Loss: 0.078513
Train Epoch: 12 [4/19 (21%)]	Train Loss: 0.139814
Train Epoch: 12 [8/19 (42%)]	Train Loss: 0.079133
Train Epoch: 12 [12/19 (63%)]	Train Loss: 0.078410
Train Epoch: 12 [16/19 (84%)]	Train Loss: 0.087206

Train set: Average loss: 0.1152, Accuracy: 65/76 (86%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(3) tensor(0) tensor(0)
tensor(11) tensor(3) tensor(2) tensor(0)
tensor(13) tensor(3) tensor(4) tensor(0)
TP= tensor(13) TN= tensor(3) FN= tensor(4) FP= tensor(0)
TP+FP tensor(13)
precision 1.0
recall 0.7647058823529411
F1 0.8666666666666666
acc 0.8
AUC 0.8823529411764706

Test set: Average loss: 0.1153, Accuracy: 16/20 (80%)

Train Epoch: 13 [0/19 (0%)]	Train Loss: 0.079170
Train Epoch: 13 [4/19 (21%)]	Train Loss: 0.116728
Train Epoch: 13 [8/19 (42%)]	Train Loss: 0.095808
Train Epoch: 13 [12/19 (63%)]	Train Loss: 0.082575
Train Epoch: 13 [16/19 (84%)]	Train Loss: 0.097570

Train set: Aver

Train Epoch: 23 [0/19 (0%)]	Train Loss: 0.079089
Train Epoch: 23 [4/19 (21%)]	Train Loss: 0.078391
Train Epoch: 23 [8/19 (42%)]	Train Loss: 0.080709
Train Epoch: 23 [12/19 (63%)]	Train Loss: 0.085855
Train Epoch: 23 [16/19 (84%)]	Train Loss: 0.095001

Train set: Average loss: 0.1428, Accuracy: 56/76 (74%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(3) tensor(0) tensor(0)
tensor(12) tensor(3) tensor(1) tensor(0)
tensor(16) tensor(3) tensor(1) tensor(0)
TP= tensor(16) TN= tensor(3) FN= tensor(1) FP= tensor(0)
TP+FP tensor(16)
precision 1.0
recall 0.9411764705882353
F1 0.9696969696969697
acc 0.95
AUC 0.9705882352941176

Test set: Average loss: 0.1019, Accuracy: 19/20 (95%)

Train Epoch: 24 [0/19 (0%)]	Train Loss: 0.079926
Train Epoch: 24 [4/19 (21%)]	Train Loss: 0.088482
Train Epoch: 24 [8/19 (42%)]	Train Loss: 0.078435
Train Epoch: 24 [12/19 (63%)]	Train Loss: 0.079508
Train Epoch: 24 [16/19 (84%)]	Train Loss: 0.078839

Train set: Ave

KeyboardInterrupt: 

In [137]:
0.1

r_list = []
p_list = []
acc_list = []
AUC_list = []


#optimizer = optim.SGD(model.parameters(), lr=0.001, momentum = 0.9)
optimizer = optim.Adam(model.parameters(), lr=0.0001)
# scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=10)
scheduler = StepLR(optimizer, step_size=1)

total_epoch = 1000
for epoch in range(1, total_epoch+1):
    train(optimizer, epoch)
    
    r, p, acc, AUC = test(epoch)
    p_list.append(p)
    r_list.append(r)
    acc_list.append(acc)
    AUC_list.append(AUC)

    # Save model
    if epoch == total_epoch:
       torch.save(model.state_dict(), "model_backup/DenseNet_{}.pt".format(epoch))  

    if epoch % 10 == 0:
        r_ave = sum(r_list)/len(r_list)
        p_ave = sum(p_list)/len(p_list)
        acc_ave = sum(acc_list)/len(acc_list)
        AUC_ave = sum(AUC_list)/len(AUC_list)
        F1_ave = 2 * r_ave * p_ave / (r_ave + p_ave)
        r_list = []
        p_list = []
        acc_list = []
        AUC_list = []
        print('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))

        f = open('model_result/DenseNet121_alpha_{}.txt'.format(alpha), 'a+')
        f.write('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))
        f.close()
# state = {'epoch': epoch + 1, 'state_dict': model.state_dict(),
#                  'optimizer': optimizer.state_dict(), 'scheduler' : scheduler}
# torch.save(state, "model_backup/AlexNetAdamState")



Train Epoch: 1 [0/19 (0%)]	Train Loss: 0.103688
Train Epoch: 1 [4/19 (21%)]	Train Loss: 0.083357
Train Epoch: 1 [8/19 (42%)]	Train Loss: 0.088995
Train Epoch: 1 [12/19 (63%)]	Train Loss: 0.082308
Train Epoch: 1 [16/19 (84%)]	Train Loss: 0.084242

Train set: Average loss: 0.1190, Accuracy: 64/76 (84%)

tensor(2) tensor(1) tensor(1) tensor(0)
tensor(5) tensor(2) tensor(1) tensor(0)
tensor(8) tensor(2) tensor(1) tensor(1)
tensor(10) tensor(2) tensor(3) tensor(1)
tensor(14) tensor(2) tensor(3) tensor(1)
TP= tensor(14) TN= tensor(2) FN= tensor(3) FP= tensor(1)
TP+FP tensor(15)
precision 0.9333333333333333
recall 0.8235294117647058
F1 0.8749999999999999
acc 0.8
AUC 0.7450980392156863

Test set: Average loss: 0.1196, Accuracy: 16/20 (80%)

Train Epoch: 2 [0/19 (0%)]	Train Loss: 0.085154
Train Epoch: 2 [4/19 (21%)]	Train Loss: 0.078859
Train Epoch: 2 [8/19 (42%)]	Train Loss: 0.092961
Train Epoch: 2 [12/19 (63%)]	Train Loss: 0.082355
Train Epoch: 2 [16/19 (84%)]	Train Loss: 0.083089

Train set:

Train Epoch: 12 [0/19 (0%)]	Train Loss: 0.086602
Train Epoch: 12 [4/19 (21%)]	Train Loss: 0.083391
Train Epoch: 12 [8/19 (42%)]	Train Loss: 0.080282
Train Epoch: 12 [12/19 (63%)]	Train Loss: 0.078540
Train Epoch: 12 [16/19 (84%)]	Train Loss: 0.078986

Train set: Average loss: 0.1142, Accuracy: 65/76 (86%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(2) tensor(0) tensor(1)
tensor(13) tensor(2) tensor(0) tensor(1)
tensor(17) tensor(2) tensor(0) tensor(1)
TP= tensor(17) TN= tensor(2) FN= tensor(0) FP= tensor(1)
TP+FP tensor(18)
precision 0.9444444444444444
recall 1.0
F1 0.9714285714285714
acc 0.95
AUC 0.8333333333333334

Test set: Average loss: 0.0999, Accuracy: 19/20 (95%)

Train Epoch: 13 [0/19 (0%)]	Train Loss: 0.078933
Train Epoch: 13 [4/19 (21%)]	Train Loss: 0.087041
Train Epoch: 13 [8/19 (42%)]	Train Loss: 0.078655
Train Epoch: 13 [12/19 (63%)]	Train Loss: 0.078796
Train Epoch: 13 [16/19 (84%)]	Train Loss: 0.080492

Train set: Ave

KeyboardInterrupt: 

In [135]:
8

r_list = []
p_list = []
acc_list = []
AUC_list = []


#optimizer = optim.SGD(model.parameters(), lr=0.001, momentum = 0.9)
optimizer = optim.Adam(model.parameters(), lr=0.0001)
# scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=10)
scheduler = StepLR(optimizer, step_size=1)

total_epoch = 1000
for epoch in range(1, total_epoch+1):
    train(optimizer, epoch)
    
    r, p, acc, AUC = test(epoch)
    p_list.append(p)
    r_list.append(r)
    acc_list.append(acc)
    AUC_list.append(AUC)

    # Save model
    if epoch == total_epoch:
       torch.save(model.state_dict(), "model_backup/DenseNet_{}.pt".format(epoch))  

    if epoch % 10 == 0:
        r_ave = sum(r_list)/len(r_list)
        p_ave = sum(p_list)/len(p_list)
        acc_ave = sum(acc_list)/len(acc_list)
        AUC_ave = sum(AUC_list)/len(AUC_list)
        F1_ave = 2 * r_ave * p_ave / (r_ave + p_ave)
        r_list = []
        p_list = []
        acc_list = []
        AUC_list = []
        print('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))

        f = open('model_result/DenseNet121_alpha_{}.txt'.format(alpha), 'a+')
        f.write('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))
        f.close()
# state = {'epoch': epoch + 1, 'state_dict': model.state_dict(),
#                  'optimizer': optimizer.state_dict(), 'scheduler' : scheduler}
# torch.save(state, "model_backup/AlexNetAdamState")



Train Epoch: 1 [0/19 (0%)]	Train Loss: 0.083270
Train Epoch: 1 [4/19 (21%)]	Train Loss: 0.085516
Train Epoch: 1 [8/19 (42%)]	Train Loss: 0.121300
Train Epoch: 1 [12/19 (63%)]	Train Loss: 0.125423
Train Epoch: 1 [16/19 (84%)]	Train Loss: 0.091340

Train set: Average loss: 0.1371, Accuracy: 55/76 (72%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(2) tensor(0) tensor(1)
tensor(13) tensor(2) tensor(0) tensor(1)
tensor(17) tensor(2) tensor(0) tensor(1)
TP= tensor(17) TN= tensor(2) FN= tensor(0) FP= tensor(1)
TP+FP tensor(18)
precision 0.9444444444444444
recall 1.0
F1 0.9714285714285714
acc 0.95
AUC 0.8333333333333334

Test set: Average loss: 0.0983, Accuracy: 19/20 (95%)

Train Epoch: 2 [0/19 (0%)]	Train Loss: 0.137494
Train Epoch: 2 [4/19 (21%)]	Train Loss: 0.131342
Train Epoch: 2 [8/19 (42%)]	Train Loss: 0.089221
Train Epoch: 2 [12/19 (63%)]	Train Loss: 0.093230
Train Epoch: 2 [16/19 (84%)]	Train Loss: 0.082248

Train set: Average loss:

Train Epoch: 12 [0/19 (0%)]	Train Loss: 0.133814
Train Epoch: 12 [4/19 (21%)]	Train Loss: 0.134802
Train Epoch: 12 [8/19 (42%)]	Train Loss: 0.158308
Train Epoch: 12 [12/19 (63%)]	Train Loss: 0.125651
Train Epoch: 12 [16/19 (84%)]	Train Loss: 0.126045

Train set: Average loss: 0.1274, Accuracy: 60/76 (79%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(3) tensor(0) tensor(0)
tensor(13) tensor(3) tensor(0) tensor(0)
tensor(16) tensor(3) tensor(1) tensor(0)
TP= tensor(16) TN= tensor(3) FN= tensor(1) FP= tensor(0)
TP+FP tensor(16)
precision 1.0
recall 0.9411764705882353
F1 0.9696969696969697
acc 0.95
AUC 0.9705882352941176

Test set: Average loss: 0.0974, Accuracy: 19/20 (95%)

Train Epoch: 13 [0/19 (0%)]	Train Loss: 0.085690
Train Epoch: 13 [4/19 (21%)]	Train Loss: 0.151658
Train Epoch: 13 [8/19 (42%)]	Train Loss: 0.123432
Train Epoch: 13 [12/19 (63%)]	Train Loss: 0.133854
Train Epoch: 13 [16/19 (84%)]	Train Loss: 0.125225

Train set: Ave

KeyboardInterrupt: 

In [133]:
0.6

r_list = []
p_list = []
acc_list = []
AUC_list = []


#optimizer = optim.SGD(model.parameters(), lr=0.001, momentum = 0.9)
optimizer = optim.Adam(model.parameters(), lr=0.0001)
# scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=10)
scheduler = StepLR(optimizer, step_size=1)

total_epoch = 1000
for epoch in range(1, total_epoch+1):
    train(optimizer, epoch)
    
    r, p, acc, AUC = test(epoch)
    p_list.append(p)
    r_list.append(r)
    acc_list.append(acc)
    AUC_list.append(AUC)

    # Save model
    if epoch == total_epoch:
       torch.save(model.state_dict(), "model_backup/DenseNet_{}.pt".format(epoch))  

    if epoch % 5 == 0:
        r_ave = sum(r_list)/len(r_list)
        p_ave = sum(p_list)/len(p_list)
        acc_ave = sum(acc_list)/len(acc_list)
        AUC_ave = sum(AUC_list)/len(AUC_list)
        F1_ave = 2 * r_ave * p_ave / (r_ave + p_ave)
        r_list = []
        p_list = []
        acc_list = []
        AUC_list = []
        print('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))

        f = open('model_result/DenseNet121_alpha_{}.txt'.format(alpha), 'a+')
        f.write('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))
        f.close()
# state = {'epoch': epoch + 1, 'state_dict': model.state_dict(),
#                  'optimizer': optimizer.state_dict(), 'scheduler' : scheduler}
# torch.save(state, "model_backup/AlexNetAdamState")



Train Epoch: 1 [0/19 (0%)]	Train Loss: 0.176852
Train Epoch: 1 [4/19 (21%)]	Train Loss: 0.172896
Train Epoch: 1 [8/19 (42%)]	Train Loss: 0.169877
Train Epoch: 1 [12/19 (63%)]	Train Loss: 0.163721
Train Epoch: 1 [16/19 (84%)]	Train Loss: 0.158067

Train set: Average loss: 0.1705, Accuracy: 46/76 (61%)

tensor(3) tensor(0) tensor(0) tensor(1)
tensor(6) tensor(0) tensor(0) tensor(2)
tensor(9) tensor(0) tensor(0) tensor(3)
tensor(13) tensor(0) tensor(0) tensor(3)
tensor(17) tensor(0) tensor(0) tensor(3)
TP= tensor(17) TN= tensor(0) FN= tensor(0) FP= tensor(3)
TP+FP tensor(20)
precision 0.85
recall 1.0
F1 0.9189189189189189
acc 0.85
AUC 0.5

Test set: Average loss: 0.1580, Accuracy: 17/20 (85%)

Train Epoch: 2 [0/19 (0%)]	Train Loss: 0.160744
Train Epoch: 2 [4/19 (21%)]	Train Loss: 0.169805
Train Epoch: 2 [8/19 (42%)]	Train Loss: 0.146349
Train Epoch: 2 [12/19 (63%)]	Train Loss: 0.155917
Train Epoch: 2 [16/19 (84%)]	Train Loss: 0.139081

Train set: Average loss: 0.1587, Accuracy: 56/76 (74%

Train Epoch: 12 [8/19 (42%)]	Train Loss: 0.150602
Train Epoch: 12 [12/19 (63%)]	Train Loss: 0.113467
Train Epoch: 12 [16/19 (84%)]	Train Loss: 0.100411

Train set: Average loss: 0.1166, Accuracy: 66/76 (87%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(2) tensor(0) tensor(1)
tensor(12) tensor(2) tensor(1) tensor(1)
tensor(16) tensor(2) tensor(1) tensor(1)
TP= tensor(16) TN= tensor(2) FN= tensor(1) FP= tensor(1)
TP+FP tensor(17)
precision 0.9411764705882353
recall 0.9411764705882353
F1 0.9411764705882353
acc 0.9
AUC 0.803921568627451

Test set: Average loss: 0.1118, Accuracy: 18/20 (90%)

Train Epoch: 13 [0/19 (0%)]	Train Loss: 0.103790
Train Epoch: 13 [4/19 (21%)]	Train Loss: 0.181304
Train Epoch: 13 [8/19 (42%)]	Train Loss: 0.164733
Train Epoch: 13 [12/19 (63%)]	Train Loss: 0.092304
Train Epoch: 13 [16/19 (84%)]	Train Loss: 0.091414

Train set: Average loss: 0.1530, Accuracy: 52/76 (68%)

tensor(3) tensor(1) tensor(0) tensor(0)
tens

Train Epoch: 23 [0/19 (0%)]	Train Loss: 0.081757
Train Epoch: 23 [4/19 (21%)]	Train Loss: 0.098208
Train Epoch: 23 [8/19 (42%)]	Train Loss: 0.097244
Train Epoch: 23 [12/19 (63%)]	Train Loss: 0.090359
Train Epoch: 23 [16/19 (84%)]	Train Loss: 0.171005

Train set: Average loss: 0.1121, Accuracy: 66/76 (87%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(2) tensor(0) tensor(1)
tensor(12) tensor(2) tensor(1) tensor(1)
tensor(16) tensor(2) tensor(1) tensor(1)
TP= tensor(16) TN= tensor(2) FN= tensor(1) FP= tensor(1)
TP+FP tensor(17)
precision 0.9411764705882353
recall 0.9411764705882353
F1 0.9411764705882353
acc 0.9
AUC 0.803921568627451

Test set: Average loss: 0.1060, Accuracy: 18/20 (90%)

Train Epoch: 24 [0/19 (0%)]	Train Loss: 0.124380
Train Epoch: 24 [4/19 (21%)]	Train Loss: 0.081684
Train Epoch: 24 [8/19 (42%)]	Train Loss: 0.279066
Train Epoch: 24 [12/19 (63%)]	Train Loss: 0.153275
Train Epoch: 24 [16/19 (84%)]	Train Loss: 0.096737

T

Train Epoch: 34 [0/19 (0%)]	Train Loss: 0.125920
Train Epoch: 34 [4/19 (21%)]	Train Loss: 0.081177
Train Epoch: 34 [8/19 (42%)]	Train Loss: 0.080970
Train Epoch: 34 [12/19 (63%)]	Train Loss: 0.126457
Train Epoch: 34 [16/19 (84%)]	Train Loss: 0.106321

Train set: Average loss: 0.1038, Accuracy: 69/76 (91%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(2) tensor(0) tensor(1)
tensor(13) tensor(2) tensor(0) tensor(1)
tensor(16) tensor(2) tensor(1) tensor(1)
TP= tensor(16) TN= tensor(2) FN= tensor(1) FP= tensor(1)
TP+FP tensor(17)
precision 0.9411764705882353
recall 0.9411764705882353
F1 0.9411764705882353
acc 0.9
AUC 0.803921568627451

Test set: Average loss: 0.1006, Accuracy: 18/20 (90%)

Train Epoch: 35 [0/19 (0%)]	Train Loss: 0.083364
Train Epoch: 35 [4/19 (21%)]	Train Loss: 0.105744
Train Epoch: 35 [8/19 (42%)]	Train Loss: 0.105652
Train Epoch: 35 [12/19 (63%)]	Train Loss: 0.089795
Train Epoch: 35 [16/19 (84%)]	Train Loss: 0.087059

T

KeyboardInterrupt: 

In [126]:
0.2


r_list = []
p_list = []
acc_list = []
AUC_list = []


#optimizer = optim.SGD(model.parameters(), lr=0.001, momentum = 0.9)
optimizer = optim.Adam(model.parameters(), lr=0.0001)
# scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=10)
scheduler = StepLR(optimizer, step_size=1)

total_epoch = 1000
for epoch in range(1, total_epoch+1):
    train(optimizer, epoch)
    
    r, p, acc, AUC = test(epoch)
    p_list.append(p)
    r_list.append(r)
    acc_list.append(acc)
    AUC_list.append(AUC)

    # Save model
    if epoch == total_epoch:
       torch.save(model.state_dict(), "model_backup/DenseNet_{}.pt".format(epoch))  

    if epoch % 5 == 0:
        r_ave = sum(r_list)/len(r_list)
        p_ave = sum(p_list)/len(p_list)
        acc_ave = sum(acc_list)/len(acc_list)
        AUC_ave = sum(AUC_list)/len(AUC_list)
        F1_ave = 2 * r_ave * p_ave / (r_ave + p_ave)
        r_list = []
        p_list = []
        acc_list = []
        AUC_list = []
        print('\n The epoch is {}, average recall: {:.4f}, average precision: {:.4f},\
average F1: {:.4f}, average accuracy: {:.4f}, average AUC: {:.4f}'.format(
        epoch, r_ave, p_ave, F1_ave, acc_ave, AUC_ave))

# state = {'epoch': epoch + 1, 'state_dict': model.state_dict(),
#                  'optimizer': optimizer.state_dict(), 'scheduler' : scheduler}
# torch.save(state, "model_backup/AlexNetAdamState")



Train Epoch: 1 [0/19 (0%)]	Train Loss: 0.036722
Train Epoch: 1 [4/19 (21%)]	Train Loss: 0.033682
Train Epoch: 1 [8/19 (42%)]	Train Loss: 0.042749
Train Epoch: 1 [12/19 (63%)]	Train Loss: 0.097011
Train Epoch: 1 [16/19 (84%)]	Train Loss: 0.007322

Train set: Average loss: 0.2276, Accuracy: 51/76 (67%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(3) tensor(0) tensor(0)
tensor(11) tensor(3) tensor(2) tensor(0)
tensor(15) tensor(3) tensor(2) tensor(0)
TP= tensor(15) TN= tensor(3) FN= tensor(2) FP= tensor(0)
TP+FP tensor(15)
precision 1.0
recall 0.8823529411764706
F1 0.9375
acc 0.9
AUC 0.9411764705882353

Test set: Average loss: 0.0569, Accuracy: 18/20 (90%)

Train Epoch: 2 [0/19 (0%)]	Train Loss: 0.054572
Train Epoch: 2 [4/19 (21%)]	Train Loss: 0.044433
Train Epoch: 2 [8/19 (42%)]	Train Loss: 0.027316
Train Epoch: 2 [12/19 (63%)]	Train Loss: 0.056991
Train Epoch: 2 [16/19 (84%)]	Train Loss: 0.039029

Train set: Average loss: 0.1445, Accu

Train Epoch: 12 [0/19 (0%)]	Train Loss: 0.007575
Train Epoch: 12 [4/19 (21%)]	Train Loss: 0.025314
Train Epoch: 12 [8/19 (42%)]	Train Loss: 0.059658
Train Epoch: 12 [12/19 (63%)]	Train Loss: 0.162872
Train Epoch: 12 [16/19 (84%)]	Train Loss: 0.066086

Train set: Average loss: 0.1789, Accuracy: 62/76 (82%)

tensor(3) tensor(0) tensor(0) tensor(1)
tensor(6) tensor(1) tensor(0) tensor(1)
tensor(9) tensor(2) tensor(0) tensor(1)
tensor(10) tensor(2) tensor(3) tensor(1)
tensor(14) tensor(2) tensor(3) tensor(1)
TP= tensor(14) TN= tensor(2) FN= tensor(3) FP= tensor(1)
TP+FP tensor(15)
precision 0.9333333333333333
recall 0.8235294117647058
F1 0.8749999999999999
acc 0.8
AUC 0.7450980392156863

Test set: Average loss: 0.0872, Accuracy: 16/20 (80%)

Train Epoch: 13 [0/19 (0%)]	Train Loss: 0.038671
Train Epoch: 13 [4/19 (21%)]	Train Loss: 0.027776
Train Epoch: 13 [8/19 (42%)]	Train Loss: 0.126252
Train Epoch: 13 [12/19 (63%)]	Train Loss: 0.075465
Train Epoch: 13 [16/19 (84%)]	Train Loss: 0.011634



Train Epoch: 23 [0/19 (0%)]	Train Loss: 0.046828
Train Epoch: 23 [4/19 (21%)]	Train Loss: 0.046305
Train Epoch: 23 [8/19 (42%)]	Train Loss: 0.015121
Train Epoch: 23 [12/19 (63%)]	Train Loss: 0.012724
Train Epoch: 23 [16/19 (84%)]	Train Loss: 0.035821

Train set: Average loss: 0.1774, Accuracy: 62/76 (82%)

tensor(3) tensor(0) tensor(0) tensor(1)
tensor(6) tensor(1) tensor(0) tensor(1)
tensor(8) tensor(2) tensor(1) tensor(1)
tensor(10) tensor(2) tensor(3) tensor(1)
tensor(14) tensor(2) tensor(3) tensor(1)
TP= tensor(14) TN= tensor(2) FN= tensor(3) FP= tensor(1)
TP+FP tensor(15)
precision 0.9333333333333333
recall 0.8235294117647058
F1 0.8749999999999999
acc 0.8
AUC 0.7450980392156863

Test set: Average loss: 0.0909, Accuracy: 16/20 (80%)

Train Epoch: 24 [0/19 (0%)]	Train Loss: 0.146997
Train Epoch: 24 [4/19 (21%)]	Train Loss: 0.028240
Train Epoch: 24 [8/19 (42%)]	Train Loss: 0.117432
Train Epoch: 24 [12/19 (63%)]	Train Loss: 0.048723
Train Epoch: 24 [16/19 (84%)]	Train Loss: 0.017895



Train Epoch: 34 [0/19 (0%)]	Train Loss: 0.156609
Train Epoch: 34 [4/19 (21%)]	Train Loss: 0.024591
Train Epoch: 34 [8/19 (42%)]	Train Loss: 0.008399
Train Epoch: 34 [12/19 (63%)]	Train Loss: 0.094690
Train Epoch: 34 [16/19 (84%)]	Train Loss: 0.015618

Train set: Average loss: 0.1285, Accuracy: 67/76 (88%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(8) tensor(3) tensor(1) tensor(0)
tensor(10) tensor(3) tensor(3) tensor(0)
tensor(14) tensor(3) tensor(3) tensor(0)
TP= tensor(14) TN= tensor(3) FN= tensor(3) FP= tensor(0)
TP+FP tensor(14)
precision 1.0
recall 0.8235294117647058
F1 0.9032258064516129
acc 0.85
AUC 0.9117647058823529

Test set: Average loss: 0.0761, Accuracy: 17/20 (85%)

Train Epoch: 35 [0/19 (0%)]	Train Loss: 0.005585
Train Epoch: 35 [4/19 (21%)]	Train Loss: 0.040076
Train Epoch: 35 [8/19 (42%)]	Train Loss: 0.021859
Train Epoch: 35 [12/19 (63%)]	Train Loss: 0.002783
Train Epoch: 35 [16/19 (84%)]	Train Loss: 0.020277

Train set: Ave

Train Epoch: 45 [0/19 (0%)]	Train Loss: 0.019002
Train Epoch: 45 [4/19 (21%)]	Train Loss: 0.004553
Train Epoch: 45 [8/19 (42%)]	Train Loss: 0.024484
Train Epoch: 45 [12/19 (63%)]	Train Loss: 0.041268
Train Epoch: 45 [16/19 (84%)]	Train Loss: 0.134697

Train set: Average loss: 0.2278, Accuracy: 61/76 (80%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(3) tensor(0) tensor(0)
tensor(11) tensor(3) tensor(2) tensor(0)
tensor(14) tensor(3) tensor(3) tensor(0)
TP= tensor(14) TN= tensor(3) FN= tensor(3) FP= tensor(0)
TP+FP tensor(14)
precision 1.0
recall 0.8235294117647058
F1 0.9032258064516129
acc 0.85
AUC 0.9117647058823529

Test set: Average loss: 0.1026, Accuracy: 17/20 (85%)


 The epoch is 45, average recall: 0.8471, average precision: 1.0000,average F1: 0.9172, average accuracy: 0.8700, average AUC: 0.9235
Train Epoch: 46 [0/19 (0%)]	Train Loss: 0.009242
Train Epoch: 46 [4/19 (21%)]	Train Loss: 0.020739
Train Epoch: 46 [8/19 (42%)]	Tra

...

Train Epoch: 287 [0/19 (0%)]	Train Loss: 0.013270
Train Epoch: 287 [4/19 (21%)]	Train Loss: 0.005585
Train Epoch: 287 [8/19 (42%)]	Train Loss: 0.013654
Train Epoch: 287 [12/19 (63%)]	Train Loss: 0.001534
Train Epoch: 287 [16/19 (84%)]	Train Loss: 0.008565

Train set: Average loss: 0.1648, Accuracy: 66/76 (87%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(3) tensor(0) tensor(0)
tensor(12) tensor(3) tensor(1) tensor(0)
tensor(15) tensor(3) tensor(2) tensor(0)
TP= tensor(15) TN= tensor(3) FN= tensor(2) FP= tensor(0)
TP+FP tensor(15)
precision 1.0
recall 0.8823529411764706
F1 0.9375
acc 0.9
AUC 0.9411764705882353

Test set: Average loss: 0.0544, Accuracy: 18/20 (90%)

Train Epoch: 288 [0/19 (0%)]	Train Loss: 0.006599
Train Epoch: 288 [4/19 (21%)]	Train Loss: 0.009130
Train Epoch: 288 [8/19 (42%)]	Train Loss: 0.018955
Train Epoch: 288 [12/19 (63%)]	Train Loss: 0.109564
Train Epoch: 288 [16/19 (84%)]	Train Loss: 0.097918

Train set: Averag

Train Epoch: 298 [0/19 (0%)]	Train Loss: 0.001721
Train Epoch: 298 [4/19 (21%)]	Train Loss: 0.020972
Train Epoch: 298 [8/19 (42%)]	Train Loss: 0.001704
Train Epoch: 298 [12/19 (63%)]	Train Loss: 0.043136
Train Epoch: 298 [16/19 (84%)]	Train Loss: 0.027597

Train set: Average loss: 0.1605, Accuracy: 63/76 (83%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(3) tensor(0) tensor(0)
tensor(12) tensor(3) tensor(1) tensor(0)
tensor(15) tensor(3) tensor(2) tensor(0)
TP= tensor(15) TN= tensor(3) FN= tensor(2) FP= tensor(0)
TP+FP tensor(15)
precision 1.0
recall 0.8823529411764706
F1 0.9375
acc 0.9
AUC 0.9411764705882353

Test set: Average loss: 0.0647, Accuracy: 18/20 (90%)

Train Epoch: 299 [0/19 (0%)]	Train Loss: 0.007521
Train Epoch: 299 [4/19 (21%)]	Train Loss: 0.008926
Train Epoch: 299 [8/19 (42%)]	Train Loss: 0.123135
Train Epoch: 299 [12/19 (63%)]	Train Loss: 0.014003
Train Epoch: 299 [16/19 (84%)]	Train Loss: 0.001760

Train set: Averag


Test set: Average loss: 0.0444, Accuracy: 19/20 (95%)

Train Epoch: 309 [0/19 (0%)]	Train Loss: 0.005751
Train Epoch: 309 [4/19 (21%)]	Train Loss: 0.003395
Train Epoch: 309 [8/19 (42%)]	Train Loss: 0.007769
Train Epoch: 309 [12/19 (63%)]	Train Loss: 0.068321
Train Epoch: 309 [16/19 (84%)]	Train Loss: 0.014549

Train set: Average loss: 0.0833, Accuracy: 69/76 (91%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(3) tensor(0) tensor(0)
tensor(13) tensor(3) tensor(0) tensor(0)
tensor(16) tensor(3) tensor(1) tensor(0)
TP= tensor(16) TN= tensor(3) FN= tensor(1) FP= tensor(0)
TP+FP tensor(16)
precision 1.0
recall 0.9411764705882353
F1 0.9696969696969697
acc 0.95
AUC 0.9705882352941176

Test set: Average loss: 0.0372, Accuracy: 19/20 (95%)

Train Epoch: 310 [0/19 (0%)]	Train Loss: 0.005744
Train Epoch: 310 [4/19 (21%)]	Train Loss: 0.004144
Train Epoch: 310 [8/19 (42%)]	Train Loss: 0.012995
Train Epoch: 310 [12/19 (63%)]	Train Loss: 0.090485
T

tensor(16) tensor(3) tensor(1) tensor(0)
TP= tensor(16) TN= tensor(3) FN= tensor(1) FP= tensor(0)
TP+FP tensor(16)
precision 1.0
recall 0.9411764705882353
F1 0.9696969696969697
acc 0.95
AUC 0.9705882352941176

Test set: Average loss: 0.0523, Accuracy: 19/20 (95%)

Train Epoch: 320 [0/19 (0%)]	Train Loss: 0.112456
Train Epoch: 320 [4/19 (21%)]	Train Loss: 0.001407
Train Epoch: 320 [8/19 (42%)]	Train Loss: 0.088852
Train Epoch: 320 [12/19 (63%)]	Train Loss: 0.003975
Train Epoch: 320 [16/19 (84%)]	Train Loss: 0.079153

Train set: Average loss: 0.0664, Accuracy: 72/76 (95%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(6) tensor(2) tensor(0) tensor(0)
tensor(9) tensor(3) tensor(0) tensor(0)
tensor(12) tensor(3) tensor(1) tensor(0)
tensor(15) tensor(3) tensor(2) tensor(0)
TP= tensor(15) TN= tensor(3) FN= tensor(2) FP= tensor(0)
TP+FP tensor(15)
precision 1.0
recall 0.8823529411764706
F1 0.9375
acc 0.9
AUC 0.9411764705882353

Test set: Average loss: 0.0673, Accuracy: 18/20 (90%)


 The epo

KeyboardInterrupt: 

In [16]:
0.4



#optimizer = optim.SGD(model.parameters(), lr=0.001, momentum = 0.9)
optimizer = optim.Adam(model.parameters(), lr=0.0001)
scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=10)
scheduler = StepLR(optimizer, step_size=1)

total_epoch = 1000
for epoch in range(1, total_epoch+1):
    train(optimizer, epoch)
    
    test(epoch)

    # Save model
    if epoch == total_epoch:
       torch.save(model.state_dict(), "model_backup/DenseNet_{}.pt".format(epoch))  


# state = {'epoch': epoch + 1, 'state_dict': model.state_dict(),
#                  'optimizer': optimizer.state_dict(), 'scheduler' : scheduler}
# torch.save(state, "model_backup/AlexNetAdamState")



Train Epoch: 1 [0/19 (0%)]	Train Loss: 0.131251
Train Epoch: 1 [4/19 (21%)]	Train Loss: 0.140185
Train Epoch: 1 [8/19 (42%)]	Train Loss: 0.144069
Train Epoch: 1 [12/19 (63%)]	Train Loss: 0.131466
Train Epoch: 1 [16/19 (84%)]	Train Loss: 0.122172

Train set: Average loss: 0.1454, Accuracy: 56/76 (74%)

tensor(3) tensor(0) tensor(0) tensor(1)
tensor(7) tensor(0) tensor(0) tensor(1)
tensor(9) tensor(0) tensor(0) tensor(3)
tensor(13) tensor(0) tensor(0) tensor(3)
tensor(16) tensor(0) tensor(0) tensor(4)
TP= tensor(16) TN= tensor(0) FN= tensor(0) FP= tensor(4)
TP+FP tensor(20)
precision 0.8
recall 1.0
F1 0.888888888888889
acc 0.8
AUC 0.5

Test set: Average loss: 0.1366, Accuracy: 16/20 (80%)

Train Epoch: 2 [0/19 (0%)]	Train Loss: 0.131341
Train Epoch: 2 [4/19 (21%)]	Train Loss: 0.119384
Train Epoch: 2 [8/19 (42%)]	Train Loss: 0.116244
Train Epoch: 2 [12/19 (63%)]	Train Loss: 0.114349
Train Epoch: 2 [16/19 (84%)]	Train Loss: 0.119674

Train set: Average loss: 0.1414, Accuracy: 61/76 (80%)



tensor(15) tensor(1) tensor(1) tensor(3)
TP= tensor(15) TN= tensor(1) FN= tensor(1) FP= tensor(3)
TP+FP tensor(18)
precision 0.8333333333333334
recall 0.9375
F1 0.8823529411764706
acc 0.8
AUC 0.59375

Test set: Average loss: 0.1243, Accuracy: 16/20 (80%)

Train Epoch: 13 [0/19 (0%)]	Train Loss: 0.091242
Train Epoch: 13 [4/19 (21%)]	Train Loss: 0.083740
Train Epoch: 13 [8/19 (42%)]	Train Loss: 0.085327
Train Epoch: 13 [12/19 (63%)]	Train Loss: 0.087535
Train Epoch: 13 [16/19 (84%)]	Train Loss: 0.191514

Train set: Average loss: 0.1131, Accuracy: 68/76 (89%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(7) tensor(1) tensor(0) tensor(0)
tensor(9) tensor(1) tensor(0) tensor(2)
tensor(12) tensor(1) tensor(1) tensor(2)
tensor(15) tensor(1) tensor(1) tensor(3)
TP= tensor(15) TN= tensor(1) FN= tensor(1) FP= tensor(3)
TP+FP tensor(18)
precision 0.8333333333333334
recall 0.9375
F1 0.8823529411764706
acc 0.8
AUC 0.59375

Test set: Average loss: 0.1222, Accuracy: 16/20 (80%)

Train Epoch: 14 [0/

Train Epoch: 24 [4/19 (21%)]	Train Loss: 0.092767
Train Epoch: 24 [8/19 (42%)]	Train Loss: 0.080572
Train Epoch: 24 [12/19 (63%)]	Train Loss: 0.123048
Train Epoch: 24 [16/19 (84%)]	Train Loss: 0.083651

Train set: Average loss: 0.1215, Accuracy: 62/76 (82%)

tensor(2) tensor(1) tensor(1) tensor(0)
tensor(6) tensor(1) tensor(1) tensor(0)
tensor(8) tensor(1) tensor(1) tensor(2)
tensor(10) tensor(1) tensor(3) tensor(2)
tensor(13) tensor(1) tensor(3) tensor(3)
TP= tensor(13) TN= tensor(1) FN= tensor(3) FP= tensor(3)
TP+FP tensor(16)
precision 0.8125
recall 0.8125
F1 0.8125
acc 0.7
AUC 0.53125

Test set: Average loss: 0.1472, Accuracy: 14/20 (70%)

Train Epoch: 25 [0/19 (0%)]	Train Loss: 0.087265
Train Epoch: 25 [4/19 (21%)]	Train Loss: 0.141400
Train Epoch: 25 [8/19 (42%)]	Train Loss: 0.129743
Train Epoch: 25 [12/19 (63%)]	Train Loss: 0.100583
Train Epoch: 25 [16/19 (84%)]	Train Loss: 0.079580

Train set: Average loss: 0.1051, Accuracy: 69/76 (91%)

tensor(3) tensor(1) tensor(0) tensor(0)


tensor(10) tensor(2) tensor(3) tensor(1)
tensor(13) tensor(2) tensor(3) tensor(2)
TP= tensor(13) TN= tensor(2) FN= tensor(3) FP= tensor(2)
TP+FP tensor(15)
precision 0.8666666666666667
recall 0.8125
F1 0.8387096774193549
acc 0.75
AUC 0.65625

Test set: Average loss: 0.1339, Accuracy: 15/20 (75%)

Train Epoch: 36 [0/19 (0%)]	Train Loss: 0.115477
Train Epoch: 36 [4/19 (21%)]	Train Loss: 0.083446
Train Epoch: 36 [8/19 (42%)]	Train Loss: 0.184316
Train Epoch: 36 [12/19 (63%)]	Train Loss: 0.131689
Train Epoch: 36 [16/19 (84%)]	Train Loss: 0.090826

Train set: Average loss: 0.1176, Accuracy: 65/76 (86%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(7) tensor(1) tensor(0) tensor(0)
tensor(9) tensor(2) tensor(0) tensor(1)
tensor(11) tensor(2) tensor(2) tensor(1)
tensor(14) tensor(2) tensor(2) tensor(2)
TP= tensor(14) TN= tensor(2) FN= tensor(2) FP= tensor(2)
TP+FP tensor(16)
precision 0.875
recall 0.875
F1 0.875
acc 0.8
AUC 0.6875

Test set: Average loss: 0.1250, Accuracy: 16/20 (80%)

Train

Train Epoch: 47 [4/19 (21%)]	Train Loss: 0.134089
Train Epoch: 47 [8/19 (42%)]	Train Loss: 0.104315
Train Epoch: 47 [12/19 (63%)]	Train Loss: 0.081183
Train Epoch: 47 [16/19 (84%)]	Train Loss: 0.080021

Train set: Average loss: 0.1294, Accuracy: 60/76 (79%)

tensor(2) tensor(1) tensor(1) tensor(0)
tensor(6) tensor(1) tensor(1) tensor(0)
tensor(8) tensor(1) tensor(1) tensor(2)
tensor(11) tensor(1) tensor(2) tensor(2)
tensor(14) tensor(1) tensor(2) tensor(3)
TP= tensor(14) TN= tensor(1) FN= tensor(2) FP= tensor(3)
TP+FP tensor(17)
precision 0.8235294117647058
recall 0.875
F1 0.8484848484848485
acc 0.75
AUC 0.5625

Test set: Average loss: 0.1316, Accuracy: 15/20 (75%)

Train Epoch: 48 [0/19 (0%)]	Train Loss: 0.111701
Train Epoch: 48 [4/19 (21%)]	Train Loss: 0.096495
Train Epoch: 48 [8/19 (42%)]	Train Loss: 0.082511
Train Epoch: 48 [12/19 (63%)]	Train Loss: 0.082224
Train Epoch: 48 [16/19 (84%)]	Train Loss: 0.127715

Train set: Average loss: 0.0932, Accuracy: 72/76 (95%)

tensor(2) tensor(

...

Train Epoch: 950 [16/19 (84%)]	Train Loss: 0.086177

Train set: Average loss: 0.1092, Accuracy: 67/76 (88%)

tensor(2) tensor(1) tensor(1) tensor(0)
tensor(6) tensor(1) tensor(1) tensor(0)
tensor(8) tensor(2) tensor(1) tensor(1)
tensor(10) tensor(2) tensor(3) tensor(1)
tensor(13) tensor(2) tensor(3) tensor(2)
TP= tensor(13) TN= tensor(2) FN= tensor(3) FP= tensor(2)
TP+FP tensor(15)
precision 0.8666666666666667
recall 0.8125
F1 0.8387096774193549
acc 0.75
AUC 0.65625

Test set: Average loss: 0.1432, Accuracy: 15/20 (75%)

Train Epoch: 951 [0/19 (0%)]	Train Loss: 0.078626
Train Epoch: 951 [4/19 (21%)]	Train Loss: 0.123361
Train Epoch: 951 [8/19 (42%)]	Train Loss: 0.078414
Train Epoch: 951 [12/19 (63%)]	Train Loss: 0.078325
Train Epoch: 951 [16/19 (84%)]	Train Loss: 0.078326

Train set: Average loss: 0.1139, Accuracy: 65/76 (86%)

tensor(2) tensor(1) tensor(1) tensor(0)
tensor(6) tensor(1) tensor(1) tensor(0)
tensor(8) tensor(2) tensor(1) tensor(1)
tensor(10) tensor(2) tensor(3) tensor(1)

tensor(9) tensor(2) tensor(4) tensor(1)
tensor(12) tensor(2) tensor(4) tensor(2)
TP= tensor(12) TN= tensor(2) FN= tensor(4) FP= tensor(2)
TP+FP tensor(14)
precision 0.8571428571428571
recall 0.75
F1 0.7999999999999999
acc 0.7
AUC 0.625

Test set: Average loss: 0.1457, Accuracy: 14/20 (70%)

Train Epoch: 962 [0/19 (0%)]	Train Loss: 0.122092
Train Epoch: 962 [4/19 (21%)]	Train Loss: 0.078364
Train Epoch: 962 [8/19 (42%)]	Train Loss: 0.116680
Train Epoch: 962 [12/19 (63%)]	Train Loss: 0.137435
Train Epoch: 962 [16/19 (84%)]	Train Loss: 0.105929

Train set: Average loss: 0.1073, Accuracy: 67/76 (88%)

tensor(2) tensor(1) tensor(1) tensor(0)
tensor(6) tensor(1) tensor(1) tensor(0)
tensor(8) tensor(2) tensor(1) tensor(1)
tensor(10) tensor(2) tensor(3) tensor(1)
tensor(13) tensor(2) tensor(3) tensor(2)
TP= tensor(13) TN= tensor(2) FN= tensor(3) FP= tensor(2)
TP+FP tensor(15)
precision 0.8666666666666667
recall 0.8125
F1 0.8387096774193549
acc 0.75
AUC 0.65625

Test set: Average loss: 0.1457, 

Train Epoch: 973 [4/19 (21%)]	Train Loss: 0.078518
Train Epoch: 973 [8/19 (42%)]	Train Loss: 0.078489
Train Epoch: 973 [12/19 (63%)]	Train Loss: 0.078464
Train Epoch: 973 [16/19 (84%)]	Train Loss: 0.082479

Train set: Average loss: 0.1242, Accuracy: 62/76 (82%)

tensor(2) tensor(1) tensor(1) tensor(0)
tensor(6) tensor(1) tensor(1) tensor(0)
tensor(8) tensor(2) tensor(1) tensor(1)
tensor(10) tensor(2) tensor(3) tensor(1)
tensor(13) tensor(2) tensor(3) tensor(2)
TP= tensor(13) TN= tensor(2) FN= tensor(3) FP= tensor(2)
TP+FP tensor(15)
precision 0.8666666666666667
recall 0.8125
F1 0.8387096774193549
acc 0.75
AUC 0.65625

Test set: Average loss: 0.1377, Accuracy: 15/20 (75%)

Train Epoch: 974 [0/19 (0%)]	Train Loss: 0.132485
Train Epoch: 974 [4/19 (21%)]	Train Loss: 0.080663
Train Epoch: 974 [8/19 (42%)]	Train Loss: 0.078834
Train Epoch: 974 [12/19 (63%)]	Train Loss: 0.114804
Train Epoch: 974 [16/19 (84%)]	Train Loss: 0.122589

Train set: Average loss: 0.1237, Accuracy: 63/76 (83%)

tensor

tensor(7) tensor(1) tensor(0) tensor(0)
tensor(9) tensor(2) tensor(0) tensor(1)
tensor(11) tensor(2) tensor(2) tensor(1)
tensor(14) tensor(2) tensor(2) tensor(2)
TP= tensor(14) TN= tensor(2) FN= tensor(2) FP= tensor(2)
TP+FP tensor(16)
precision 0.875
recall 0.875
F1 0.875
acc 0.8
AUC 0.6875

Test set: Average loss: 0.1313, Accuracy: 16/20 (80%)

Train Epoch: 985 [0/19 (0%)]	Train Loss: 0.078330
Train Epoch: 985 [4/19 (21%)]	Train Loss: 0.078358
Train Epoch: 985 [8/19 (42%)]	Train Loss: 0.133984
Train Epoch: 985 [12/19 (63%)]	Train Loss: 0.079745
Train Epoch: 985 [16/19 (84%)]	Train Loss: 0.079196

Train set: Average loss: 0.1206, Accuracy: 63/76 (83%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(7) tensor(1) tensor(0) tensor(0)
tensor(9) tensor(2) tensor(0) tensor(1)
tensor(11) tensor(2) tensor(2) tensor(1)
tensor(14) tensor(2) tensor(2) tensor(2)
TP= tensor(14) TN= tensor(2) FN= tensor(2) FP= tensor(2)
TP+FP tensor(16)
precision 0.875
recall 0.875
F1 0.875
acc 0.8
AUC 0.6875

Test

Train Epoch: 996 [12/19 (63%)]	Train Loss: 0.078572
Train Epoch: 996 [16/19 (84%)]	Train Loss: 0.078583

Train set: Average loss: 0.1048, Accuracy: 68/76 (89%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(7) tensor(1) tensor(0) tensor(0)
tensor(9) tensor(2) tensor(0) tensor(1)
tensor(11) tensor(2) tensor(2) tensor(1)
tensor(14) tensor(2) tensor(2) tensor(2)
TP= tensor(14) TN= tensor(2) FN= tensor(2) FP= tensor(2)
TP+FP tensor(16)
precision 0.875
recall 0.875
F1 0.875
acc 0.8
AUC 0.6875

Test set: Average loss: 0.1289, Accuracy: 16/20 (80%)

Train Epoch: 997 [0/19 (0%)]	Train Loss: 0.078318
Train Epoch: 997 [4/19 (21%)]	Train Loss: 0.078436
Train Epoch: 997 [8/19 (42%)]	Train Loss: 0.089611
Train Epoch: 997 [12/19 (63%)]	Train Loss: 0.078441
Train Epoch: 997 [16/19 (84%)]	Train Loss: 0.078810

Train set: Average loss: 0.0974, Accuracy: 70/76 (92%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(7) tensor(1) tensor(0) tensor(0)
tensor(9) tensor(2) tensor(0) tensor(1)
tensor(11) tensor

In [47]:
        
#optimizer = optim.SGD(model.parameters(), lr=0.001, momentum = 0.9)
optimizer = optim.Adam(model.parameters(), lr=0.0001)
scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=10)
scheduler = StepLR(optimizer, step_size=1)

for epoch in range(1, 1000+1):
    train(optimizer, epoch)
    
    test(epoch)

    # Save model
    torch.save(model.state_dict(), "model_backup/DenseNet_{}.pt".format(epoch))  


# state = {'epoch': epoch + 1, 'state_dict': model.state_dict(),
#                  'optimizer': optimizer.state_dict(), 'scheduler' : scheduler}
# torch.save(state, "model_backup/AlexNetAdamState")

Train Epoch: 1 [0/19 (0%)]	Train Loss: 0.078586
Train Epoch: 1 [4/19 (21%)]	Train Loss: 0.083751
Train Epoch: 1 [8/19 (42%)]	Train Loss: 0.079853
Train Epoch: 1 [12/19 (63%)]	Train Loss: 0.126858
Train Epoch: 1 [16/19 (84%)]	Train Loss: 0.078486

Train set: Average loss: 0.1072, Accuracy: 65/73 (89%)

tensor(3) tensor(0) tensor(0) tensor(1)
tensor(4) tensor(1) tensor(0) tensor(3)
tensor(7) tensor(1) tensor(1) tensor(3)
tensor(10) tensor(1) tensor(2) tensor(3)
tensor(13) tensor(1) tensor(2) tensor(3)
TP= tensor(13) TN= tensor(1) FN= tensor(2) FP= tensor(3)
TP+FP tensor(16)
precision 0.8125
recall 0.8666666666666667
F1 0.8387096774193549
acc 0.7368421052631579
AUC 0.5583333333333333

Test set: Average loss: 0.1337, Accuracy: 14/19 (74%)

Train Epoch: 2 [0/19 (0%)]	Train Loss: 0.116327
Train Epoch: 2 [4/19 (21%)]	Train Loss: 0.078409
Train Epoch: 2 [8/19 (42%)]	Train Loss: 0.078432
Train Epoch: 2 [12/19 (63%)]	Train Loss: 0.078386
Train Epoch: 2 [16/19 (84%)]	Train Loss: 0.078332

Train s

Train Epoch: 12 [0/19 (0%)]	Train Loss: 0.078366
Train Epoch: 12 [4/19 (21%)]	Train Loss: 0.078321
Train Epoch: 12 [8/19 (42%)]	Train Loss: 0.078365
Train Epoch: 12 [12/19 (63%)]	Train Loss: 0.078372
Train Epoch: 12 [16/19 (84%)]	Train Loss: 0.078685

Train set: Average loss: 0.1071, Accuracy: 65/73 (89%)

tensor(3) tensor(0) tensor(0) tensor(1)
tensor(4) tensor(1) tensor(0) tensor(3)
tensor(7) tensor(1) tensor(1) tensor(3)
tensor(11) tensor(1) tensor(1) tensor(3)
tensor(14) tensor(1) tensor(1) tensor(3)
TP= tensor(14) TN= tensor(1) FN= tensor(1) FP= tensor(3)
TP+FP tensor(17)
precision 0.8235294117647058
recall 0.9333333333333333
F1 0.8749999999999999
acc 0.7894736842105263
AUC 0.5916666666666667

Test set: Average loss: 0.1241, Accuracy: 15/19 (79%)

Train Epoch: 13 [0/19 (0%)]	Train Loss: 0.078737
Train Epoch: 13 [4/19 (21%)]	Train Loss: 0.154131
Train Epoch: 13 [8/19 (42%)]	Train Loss: 0.084458
Train Epoch: 13 [12/19 (63%)]	Train Loss: 0.078336
Train Epoch: 13 [16/19 (84%)]	Train L

Train Epoch: 23 [0/19 (0%)]	Train Loss: 0.081190
Train Epoch: 23 [4/19 (21%)]	Train Loss: 0.078362
Train Epoch: 23 [8/19 (42%)]	Train Loss: 0.078816
Train Epoch: 23 [12/19 (63%)]	Train Loss: 0.083298
Train Epoch: 23 [16/19 (84%)]	Train Loss: 0.087197

Train set: Average loss: 0.1343, Accuracy: 56/73 (77%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(4) tensor(2) tensor(0) tensor(2)
tensor(7) tensor(2) tensor(1) tensor(2)
tensor(11) tensor(2) tensor(1) tensor(2)
tensor(14) tensor(2) tensor(1) tensor(2)
TP= tensor(14) TN= tensor(2) FN= tensor(1) FP= tensor(2)
TP+FP tensor(16)
precision 0.875
recall 0.9333333333333333
F1 0.9032258064516129
acc 0.8421052631578947
AUC 0.7166666666666667

Test set: Average loss: 0.1235, Accuracy: 16/19 (84%)

Train Epoch: 24 [0/19 (0%)]	Train Loss: 0.078446
Train Epoch: 24 [4/19 (21%)]	Train Loss: 0.087478
Train Epoch: 24 [8/19 (42%)]	Train Loss: 0.079008
Train Epoch: 24 [12/19 (63%)]	Train Loss: 0.137881
Train Epoch: 24 [16/19 (84%)]	Train Loss: 0.078328

Train Epoch: 34 [0/19 (0%)]	Train Loss: 0.092107
Train Epoch: 34 [4/19 (21%)]	Train Loss: 0.078403
Train Epoch: 34 [8/19 (42%)]	Train Loss: 0.078387
Train Epoch: 34 [12/19 (63%)]	Train Loss: 0.078367
Train Epoch: 34 [16/19 (84%)]	Train Loss: 0.108527

Train set: Average loss: 0.1159, Accuracy: 66/73 (90%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(4) tensor(2) tensor(0) tensor(2)
tensor(7) tensor(2) tensor(1) tensor(2)
tensor(11) tensor(2) tensor(1) tensor(2)
tensor(14) tensor(2) tensor(1) tensor(2)
TP= tensor(14) TN= tensor(2) FN= tensor(1) FP= tensor(2)
TP+FP tensor(16)
precision 0.875
recall 0.9333333333333333
F1 0.9032258064516129
acc 0.8421052631578947
AUC 0.7166666666666667

Test set: Average loss: 0.1196, Accuracy: 16/19 (84%)

Train Epoch: 35 [0/19 (0%)]	Train Loss: 0.078386
Train Epoch: 35 [4/19 (21%)]	Train Loss: 0.093149
Train Epoch: 35 [8/19 (42%)]	Train Loss: 0.078400
Train Epoch: 35 [12/19 (63%)]	Train Loss: 0.078566
Train Epoch: 35 [16/19 (84%)]	Train Loss: 0.078780

Train Epoch: 45 [0/19 (0%)]	Train Loss: 0.117631
Train Epoch: 45 [4/19 (21%)]	Train Loss: 0.078442
Train Epoch: 45 [8/19 (42%)]	Train Loss: 0.078382
Train Epoch: 45 [12/19 (63%)]	Train Loss: 0.129281
Train Epoch: 45 [16/19 (84%)]	Train Loss: 0.078457

Train set: Average loss: 0.1109, Accuracy: 65/73 (89%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(4) tensor(3) tensor(0) tensor(1)
tensor(7) tensor(3) tensor(1) tensor(1)
tensor(11) tensor(3) tensor(1) tensor(1)
tensor(14) tensor(3) tensor(1) tensor(1)
TP= tensor(14) TN= tensor(3) FN= tensor(1) FP= tensor(1)
TP+FP tensor(15)
precision 0.9333333333333333
recall 0.9333333333333333
F1 0.9333333333333333
acc 0.8947368421052632
AUC 0.8416666666666667

Test set: Average loss: 0.1060, Accuracy: 17/19 (89%)

Train Epoch: 46 [0/19 (0%)]	Train Loss: 0.100713
Train Epoch: 46 [4/19 (21%)]	Train Loss: 0.081040
Train Epoch: 46 [8/19 (42%)]	Train Loss: 0.078465
Train Epoch: 46 [12/19 (63%)]	Train Loss: 0.079269
Train Epoch: 46 [16/19 (84%)]	Train L

...

Train Epoch: 946 [0/19 (0%)]	Train Loss: 0.078419
Train Epoch: 946 [4/19 (21%)]	Train Loss: 0.078333
Train Epoch: 946 [8/19 (42%)]	Train Loss: 0.078322
Train Epoch: 946 [12/19 (63%)]	Train Loss: 0.084412
Train Epoch: 946 [16/19 (84%)]	Train Loss: 0.078317

Train set: Average loss: 0.1144, Accuracy: 64/73 (88%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(4) tensor(3) tensor(0) tensor(1)
tensor(7) tensor(3) tensor(1) tensor(1)
tensor(11) tensor(3) tensor(1) tensor(1)
tensor(13) tensor(3) tensor(2) tensor(1)
TP= tensor(13) TN= tensor(3) FN= tensor(2) FP= tensor(1)
TP+FP tensor(14)
precision 0.9285714285714286
recall 0.8666666666666667
F1 0.896551724137931
acc 0.8421052631578947
AUC 0.8083333333333333

Test set: Average loss: 0.1213, Accuracy: 16/19 (84%)

Train Epoch: 947 [0/19 (0%)]	Train Loss: 0.080904
Train Epoch: 947 [4/19 (21%)]	Train Loss: 0.078353
Train Epoch: 947 [8/19 (42%)]	Train Loss: 0.098487
Train Epoch: 947 [12/19 (63%)]	Train Loss: 0.078329
Train Epoch: 947 [16/19 (84%)

Train Epoch: 957 [0/19 (0%)]	Train Loss: 0.079843
Train Epoch: 957 [4/19 (21%)]	Train Loss: 0.124205
Train Epoch: 957 [8/19 (42%)]	Train Loss: 0.078436
Train Epoch: 957 [12/19 (63%)]	Train Loss: 0.078388
Train Epoch: 957 [16/19 (84%)]	Train Loss: 0.114060

Train set: Average loss: 0.1159, Accuracy: 63/73 (86%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(4) tensor(4) tensor(0) tensor(0)
tensor(7) tensor(4) tensor(1) tensor(0)
tensor(11) tensor(4) tensor(1) tensor(0)
tensor(13) tensor(4) tensor(2) tensor(0)
TP= tensor(13) TN= tensor(4) FN= tensor(2) FP= tensor(0)
TP+FP tensor(13)
precision 1.0
recall 0.8666666666666667
F1 0.9285714285714286
acc 0.8947368421052632
AUC 0.9333333333333333

Test set: Average loss: 0.1154, Accuracy: 17/19 (89%)

Train Epoch: 958 [0/19 (0%)]	Train Loss: 0.083339
Train Epoch: 958 [4/19 (21%)]	Train Loss: 0.083872
Train Epoch: 958 [8/19 (42%)]	Train Loss: 0.103550
Train Epoch: 958 [12/19 (63%)]	Train Loss: 0.078320
Train Epoch: 958 [16/19 (84%)]	Train Loss: 

Train Epoch: 968 [0/19 (0%)]	Train Loss: 0.079130
Train Epoch: 968 [4/19 (21%)]	Train Loss: 0.115367
Train Epoch: 968 [8/19 (42%)]	Train Loss: 0.137875
Train Epoch: 968 [12/19 (63%)]	Train Loss: 0.078959
Train Epoch: 968 [16/19 (84%)]	Train Loss: 0.083552

Train set: Average loss: 0.1293, Accuracy: 59/73 (81%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(4) tensor(4) tensor(0) tensor(0)
tensor(7) tensor(4) tensor(1) tensor(0)
tensor(9) tensor(4) tensor(3) tensor(0)
tensor(11) tensor(4) tensor(4) tensor(0)
TP= tensor(11) TN= tensor(4) FN= tensor(4) FP= tensor(0)
TP+FP tensor(11)
precision 1.0
recall 0.7333333333333333
F1 0.846153846153846
acc 0.7894736842105263
AUC 0.8666666666666667

Test set: Average loss: 0.1441, Accuracy: 15/19 (79%)

Train Epoch: 969 [0/19 (0%)]	Train Loss: 0.078598
Train Epoch: 969 [4/19 (21%)]	Train Loss: 0.078522
Train Epoch: 969 [8/19 (42%)]	Train Loss: 0.089286
Train Epoch: 969 [12/19 (63%)]	Train Loss: 0.082667
Train Epoch: 969 [16/19 (84%)]	Train Loss: 0.

Train Epoch: 979 [0/19 (0%)]	Train Loss: 0.131672
Train Epoch: 979 [4/19 (21%)]	Train Loss: 0.094071
Train Epoch: 979 [8/19 (42%)]	Train Loss: 0.078321
Train Epoch: 979 [12/19 (63%)]	Train Loss: 0.078427
Train Epoch: 979 [16/19 (84%)]	Train Loss: 0.078462

Train set: Average loss: 0.1363, Accuracy: 57/73 (78%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(4) tensor(3) tensor(0) tensor(1)
tensor(7) tensor(3) tensor(1) tensor(1)
tensor(11) tensor(3) tensor(1) tensor(1)
tensor(13) tensor(3) tensor(2) tensor(1)
TP= tensor(13) TN= tensor(3) FN= tensor(2) FP= tensor(1)
TP+FP tensor(14)
precision 0.9285714285714286
recall 0.8666666666666667
F1 0.896551724137931
acc 0.8421052631578947
AUC 0.8083333333333333

Test set: Average loss: 0.1222, Accuracy: 16/19 (84%)

Train Epoch: 980 [0/19 (0%)]	Train Loss: 0.078460
Train Epoch: 980 [4/19 (21%)]	Train Loss: 0.078998
Train Epoch: 980 [8/19 (42%)]	Train Loss: 0.138214
Train Epoch: 980 [12/19 (63%)]	Train Loss: 0.078319
Train Epoch: 980 [16/19 (84%)

Train Epoch: 990 [0/19 (0%)]	Train Loss: 0.082188
Train Epoch: 990 [4/19 (21%)]	Train Loss: 0.089106
Train Epoch: 990 [8/19 (42%)]	Train Loss: 0.078331
Train Epoch: 990 [12/19 (63%)]	Train Loss: 0.078368
Train Epoch: 990 [16/19 (84%)]	Train Loss: 0.106401

Train set: Average loss: 0.1227, Accuracy: 61/73 (84%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(4) tensor(3) tensor(0) tensor(1)
tensor(7) tensor(3) tensor(1) tensor(1)
tensor(11) tensor(3) tensor(1) tensor(1)
tensor(14) tensor(3) tensor(1) tensor(1)
TP= tensor(14) TN= tensor(3) FN= tensor(1) FP= tensor(1)
TP+FP tensor(15)
precision 0.9333333333333333
recall 0.9333333333333333
F1 0.9333333333333333
acc 0.8947368421052632
AUC 0.8416666666666667

Test set: Average loss: 0.1155, Accuracy: 17/19 (89%)

Train Epoch: 991 [0/19 (0%)]	Train Loss: 0.078317
Train Epoch: 991 [4/19 (21%)]	Train Loss: 0.123587
Train Epoch: 991 [8/19 (42%)]	Train Loss: 0.078610
Train Epoch: 991 [12/19 (63%)]	Train Loss: 0.078372
Train Epoch: 991 [16/19 (84%

In [45]:
        
#optimizer = optim.SGD(model.parameters(), lr=0.001, momentum = 0.9)
optimizer = optim.Adam(model.parameters(), lr=0.0001)
scheduler = optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=10)
scheduler = StepLR(optimizer, step_size=1)

for epoch in range(1, 1000+1):
    train(optimizer, epoch)
    
    test(epoch)

    # Save model
    torch.save(model.state_dict(), "model_backup/DenseNet_{}.pt".format(epoch))  


# state = {'epoch': epoch + 1, 'state_dict': model.state_dict(),
#                  'optimizer': optimizer.state_dict(), 'scheduler' : scheduler}
# torch.save(state, "model_backup/AlexNetAdamState")

Train Epoch: 1 [0/19 (0%)]	Train Loss: 0.084299
Train Epoch: 1 [4/19 (21%)]	Train Loss: 0.086293
Train Epoch: 1 [8/19 (42%)]	Train Loss: 0.090824
Train Epoch: 1 [12/19 (63%)]	Train Loss: 0.094682
Train Epoch: 1 [16/19 (84%)]	Train Loss: 0.101363

Train set: Average loss: 0.1364, Accuracy: 56/73 (77%)

tensor(3) tensor(0) tensor(0) tensor(1)
tensor(4) tensor(2) tensor(0) tensor(2)
tensor(7) tensor(2) tensor(1) tensor(2)
tensor(10) tensor(2) tensor(2) tensor(2)
tensor(13) tensor(2) tensor(2) tensor(2)
TP= tensor(13) TN= tensor(2) FN= tensor(2) FP= tensor(2)
TP+FP tensor(15)
precision 0.8666666666666667
recall 0.8666666666666667
F1 0.8666666666666667
acc 0.7894736842105263
AUC 0.6833333333333333

Test set: Average loss: 0.1223, Accuracy: 15/19 (79%)

Train Epoch: 2 [0/19 (0%)]	Train Loss: 0.081280
Train Epoch: 2 [4/19 (21%)]	Train Loss: 0.082345
Train Epoch: 2 [8/19 (42%)]	Train Loss: 0.086973
Train Epoch: 2 [12/19 (63%)]	Train Loss: 0.086852
Train Epoch: 2 [16/19 (84%)]	Train Loss: 0.120

Train Epoch: 12 [0/19 (0%)]	Train Loss: 0.121108
Train Epoch: 12 [4/19 (21%)]	Train Loss: 0.081391
Train Epoch: 12 [8/19 (42%)]	Train Loss: 0.080523
Train Epoch: 12 [12/19 (63%)]	Train Loss: 0.141098
Train Epoch: 12 [16/19 (84%)]	Train Loss: 0.118346

Train set: Average loss: 0.1598, Accuracy: 52/73 (71%)

tensor(3) tensor(0) tensor(0) tensor(1)
tensor(4) tensor(2) tensor(0) tensor(2)
tensor(8) tensor(2) tensor(0) tensor(2)
tensor(12) tensor(2) tensor(0) tensor(2)
tensor(15) tensor(2) tensor(0) tensor(2)
TP= tensor(15) TN= tensor(2) FN= tensor(0) FP= tensor(2)
TP+FP tensor(17)
precision 0.8823529411764706
recall 1.0
F1 0.9375
acc 0.8947368421052632
AUC 0.75

Test set: Average loss: 0.1096, Accuracy: 17/19 (89%)

Train Epoch: 13 [0/19 (0%)]	Train Loss: 0.082243
Train Epoch: 13 [4/19 (21%)]	Train Loss: 0.084005
Train Epoch: 13 [8/19 (42%)]	Train Loss: 0.080084
Train Epoch: 13 [12/19 (63%)]	Train Loss: 0.082479
Train Epoch: 13 [16/19 (84%)]	Train Loss: 0.091691

Train set: Average loss: 0

Train Epoch: 23 [0/19 (0%)]	Train Loss: 0.141213
Train Epoch: 23 [4/19 (21%)]	Train Loss: 0.124884
Train Epoch: 23 [8/19 (42%)]	Train Loss: 0.078788
Train Epoch: 23 [12/19 (63%)]	Train Loss: 0.191817
Train Epoch: 23 [16/19 (84%)]	Train Loss: 0.101307

Train set: Average loss: 0.1309, Accuracy: 58/73 (79%)

tensor(3) tensor(0) tensor(0) tensor(1)
tensor(4) tensor(3) tensor(0) tensor(1)
tensor(7) tensor(3) tensor(1) tensor(1)
tensor(11) tensor(3) tensor(1) tensor(1)
tensor(14) tensor(3) tensor(1) tensor(1)
TP= tensor(14) TN= tensor(3) FN= tensor(1) FP= tensor(1)
TP+FP tensor(15)
precision 0.9333333333333333
recall 0.9333333333333333
F1 0.9333333333333333
acc 0.8947368421052632
AUC 0.8416666666666667

Test set: Average loss: 0.1094, Accuracy: 17/19 (89%)

Train Epoch: 24 [0/19 (0%)]	Train Loss: 0.078878
Train Epoch: 24 [4/19 (21%)]	Train Loss: 0.135492
Train Epoch: 24 [8/19 (42%)]	Train Loss: 0.112993
Train Epoch: 24 [12/19 (63%)]	Train Loss: 0.082047
Train Epoch: 24 [16/19 (84%)]	Train L

Train Epoch: 34 [0/19 (0%)]	Train Loss: 0.078750
Train Epoch: 34 [4/19 (21%)]	Train Loss: 0.079248
Train Epoch: 34 [8/19 (42%)]	Train Loss: 0.124888
Train Epoch: 34 [12/19 (63%)]	Train Loss: 0.080383
Train Epoch: 34 [16/19 (84%)]	Train Loss: 0.084136

Train set: Average loss: 0.1329, Accuracy: 58/73 (79%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(4) tensor(2) tensor(0) tensor(2)
tensor(7) tensor(2) tensor(1) tensor(2)
tensor(10) tensor(2) tensor(2) tensor(2)
tensor(13) tensor(2) tensor(2) tensor(2)
TP= tensor(13) TN= tensor(2) FN= tensor(2) FP= tensor(2)
TP+FP tensor(15)
precision 0.8666666666666667
recall 0.8666666666666667
F1 0.8666666666666667
acc 0.7894736842105263
AUC 0.6833333333333333

Test set: Average loss: 0.1358, Accuracy: 15/19 (79%)

Train Epoch: 35 [0/19 (0%)]	Train Loss: 0.079047
Train Epoch: 35 [4/19 (21%)]	Train Loss: 0.120116
Train Epoch: 35 [8/19 (42%)]	Train Loss: 0.080060
Train Epoch: 35 [12/19 (63%)]	Train Loss: 0.079046
Train Epoch: 35 [16/19 (84%)]	Train L

Train Epoch: 45 [0/19 (0%)]	Train Loss: 0.106443
Train Epoch: 45 [4/19 (21%)]	Train Loss: 0.099734
Train Epoch: 45 [8/19 (42%)]	Train Loss: 0.098973
Train Epoch: 45 [12/19 (63%)]	Train Loss: 0.079234
Train Epoch: 45 [16/19 (84%)]	Train Loss: 0.102440

Train set: Average loss: 0.1263, Accuracy: 60/73 (82%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(4) tensor(3) tensor(0) tensor(1)
tensor(7) tensor(3) tensor(1) tensor(1)
tensor(10) tensor(3) tensor(2) tensor(1)
tensor(13) tensor(3) tensor(2) tensor(1)
TP= tensor(13) TN= tensor(3) FN= tensor(2) FP= tensor(1)
TP+FP tensor(14)
precision 0.9285714285714286
recall 0.8666666666666667
F1 0.896551724137931
acc 0.8421052631578947
AUC 0.8083333333333333

Test set: Average loss: 0.1227, Accuracy: 16/19 (84%)

Train Epoch: 46 [0/19 (0%)]	Train Loss: 0.079577
Train Epoch: 46 [4/19 (21%)]	Train Loss: 0.078954
Train Epoch: 46 [8/19 (42%)]	Train Loss: 0.082125
Train Epoch: 46 [12/19 (63%)]	Train Loss: 0.099967
Train Epoch: 46 [16/19 (84%)]	Train Lo

...

Train Epoch: 188 [0/19 (0%)]	Train Loss: 0.078758
Train Epoch: 188 [4/19 (21%)]	Train Loss: 0.085596
Train Epoch: 188 [8/19 (42%)]	Train Loss: 0.078392
Train Epoch: 188 [12/19 (63%)]	Train Loss: 0.078666
Train Epoch: 188 [16/19 (84%)]	Train Loss: 0.130481

Train set: Average loss: 0.1351, Accuracy: 56/73 (77%)

tensor(3) tensor(0) tensor(0) tensor(1)
tensor(4) tensor(1) tensor(0) tensor(3)
tensor(7) tensor(1) tensor(1) tensor(3)
tensor(10) tensor(1) tensor(2) tensor(3)
tensor(13) tensor(1) tensor(2) tensor(3)
TP= tensor(13) TN= tensor(1) FN= tensor(2) FP= tensor(3)
TP+FP tensor(16)
precision 0.8125
recall 0.8666666666666667
F1 0.8387096774193549
acc 0.7368421052631579
AUC 0.5583333333333333

Test set: Average loss: 0.1295, Accuracy: 14/19 (74%)

Train Epoch: 189 [0/19 (0%)]	Train Loss: 0.078608
Train Epoch: 189 [4/19 (21%)]	Train Loss: 0.078500
Train Epoch: 189 [8/19 (42%)]	Train Loss: 0.078519
Train Epoch: 189 [12/19 (63%)]	Train Loss: 0.078432
Train Epoch: 189 [16/19 (84%)]	Train Los

Train Epoch: 199 [0/19 (0%)]	Train Loss: 0.103087
Train Epoch: 199 [4/19 (21%)]	Train Loss: 0.079265
Train Epoch: 199 [8/19 (42%)]	Train Loss: 0.078533
Train Epoch: 199 [12/19 (63%)]	Train Loss: 0.126287
Train Epoch: 199 [16/19 (84%)]	Train Loss: 0.220833

Train set: Average loss: 0.1192, Accuracy: 62/73 (85%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(4) tensor(2) tensor(0) tensor(2)
tensor(7) tensor(2) tensor(1) tensor(2)
tensor(10) tensor(2) tensor(2) tensor(2)
tensor(13) tensor(2) tensor(2) tensor(2)
TP= tensor(13) TN= tensor(2) FN= tensor(2) FP= tensor(2)
TP+FP tensor(15)
precision 0.8666666666666667
recall 0.8666666666666667
F1 0.8666666666666667
acc 0.7894736842105263
AUC 0.6833333333333333

Test set: Average loss: 0.1341, Accuracy: 15/19 (79%)

Train Epoch: 200 [0/19 (0%)]	Train Loss: 0.079177
Train Epoch: 200 [4/19 (21%)]	Train Loss: 0.118553
Train Epoch: 200 [8/19 (42%)]	Train Loss: 0.083613
Train Epoch: 200 [12/19 (63%)]	Train Loss: 0.078488
Train Epoch: 200 [16/19 (84%

Train Epoch: 210 [0/19 (0%)]	Train Loss: 0.089215
Train Epoch: 210 [4/19 (21%)]	Train Loss: 0.079140
Train Epoch: 210 [8/19 (42%)]	Train Loss: 0.078403
Train Epoch: 210 [12/19 (63%)]	Train Loss: 0.085246
Train Epoch: 210 [16/19 (84%)]	Train Loss: 0.078449

Train set: Average loss: 0.1352, Accuracy: 57/73 (78%)

tensor(3) tensor(1) tensor(0) tensor(0)
tensor(4) tensor(3) tensor(0) tensor(1)
tensor(7) tensor(3) tensor(1) tensor(1)
tensor(11) tensor(3) tensor(1) tensor(1)
tensor(14) tensor(3) tensor(1) tensor(1)
TP= tensor(14) TN= tensor(3) FN= tensor(1) FP= tensor(1)
TP+FP tensor(15)
precision 0.9333333333333333
recall 0.9333333333333333
F1 0.9333333333333333
acc 0.8947368421052632
AUC 0.8416666666666667

Test set: Average loss: 0.1129, Accuracy: 17/19 (89%)

Train Epoch: 211 [0/19 (0%)]	Train Loss: 0.092572
Train Epoch: 211 [4/19 (21%)]	Train Loss: 0.132355
Train Epoch: 211 [8/19 (42%)]	Train Loss: 0.109586
Train Epoch: 211 [12/19 (63%)]	Train Loss: 0.078488
Train Epoch: 211 [16/19 (84%

Train Epoch: 221 [0/19 (0%)]	Train Loss: 0.118968
Train Epoch: 221 [4/19 (21%)]	Train Loss: 0.099752
Train Epoch: 221 [8/19 (42%)]	Train Loss: 0.115940
Train Epoch: 221 [12/19 (63%)]	Train Loss: 0.140238
Train Epoch: 221 [16/19 (84%)]	Train Loss: 0.129756

Train set: Average loss: 0.1388, Accuracy: 56/73 (77%)

tensor(3) tensor(0) tensor(0) tensor(1)
tensor(4) tensor(2) tensor(0) tensor(2)
tensor(7) tensor(2) tensor(1) tensor(2)
tensor(11) tensor(2) tensor(1) tensor(2)
tensor(14) tensor(2) tensor(1) tensor(2)
TP= tensor(14) TN= tensor(2) FN= tensor(1) FP= tensor(2)
TP+FP tensor(16)
precision 0.875
recall 0.9333333333333333
F1 0.9032258064516129
acc 0.8421052631578947
AUC 0.7166666666666667

Test set: Average loss: 0.1221, Accuracy: 16/19 (84%)

Train Epoch: 222 [0/19 (0%)]	Train Loss: 0.078368
Train Epoch: 222 [4/19 (21%)]	Train Loss: 0.127900
Train Epoch: 222 [8/19 (42%)]	Train Loss: 0.079204
Train Epoch: 222 [12/19 (63%)]	Train Loss: 0.078325
Train Epoch: 222 [16/19 (84%)]	Train Loss

KeyboardInterrupt: 

In [19]:
        
#optimizer = optim.SGD(model.parameters(), lr=0.001, momentum = 0.9)
optimizer = optim.Adam(model.parameters(), lr=0.0001)
scheduler = StepLR(optimizer, step_size=1)

for epoch in range(1, 100+1):
    train(optimizer, epoch)
    
    test(epoch)

    # Save model
#     torch.save(model.state_dict(), "model_backup/AlexNet_3_class_xray_cnn_{}.pt".format(epoch))  


# state = {'epoch': epoch + 1, 'state_dict': model.state_dict(),
#                  'optimizer': optimizer.state_dict(), 'scheduler' : scheduler}
# torch.save(state, "model_backup/AlexNetAdamState")

NameError: name 'args' is not defined